<a href="https://colab.research.google.com/github/minkyunglee-data/Team_project/blob/main/EV_charging_station_in_Daegu_location_analysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#**Floating population by District**

In [ ]:
import folium
from folium.plugins import MarkerCluster
import json
import pandas as pd

In [ ]:
df1 = pd.read_csv("/content/행정구역_읍면동_별_5세별_주민등록인구_2024년3월.csv", encoding='cp949')
df2 = pd.read_csv("/content/대구광역시_읍면동코드.csv", encoding='cp949')

##데이터 전처리

In [ ]:
# df1 전처리: 첫 행 삭제, 첫 두 컬럼 선택 후 컬럼명을 "읍면동 코드"와 "인구수"로 변경
df1 = df1.iloc[1:, :2]
df1.columns = ['읍면동 코드', '인구수']

# join key인 '읍면동 코드'는 병합을 위해 문자열로 변환
df1['읍면동 코드'] = df1['읍면동 코드'].astype(str)

# 인구수 컬럼은 숫자형으로 변환
df1['인구수'] = pd.to_numeric(df1['인구수'], errors='coerce')

# df2 'dong' 컬럼을 문자열로 변환하고, 필요한 컬럼만 선택
df2['dong'] = df2['dong'].astype(str)
df2_subset = df2[['dong', 'adm_cd']]

# adm_cd도 숫자형으로 변환 (병합 후 Choropleth에서 사용하기 위함)
df2_subset = df2[['dong', 'adm_cd']].copy()
df2_subset['adm_cd'] = pd.to_numeric(df2_subset['adm_cd'], errors='coerce')

# df1과 df2_subset을 '읍면동 코드'(df1)와 'dong'(df2)를 기준으로 레프트 조인
df = pd.merge(df1, df2_subset, left_on='읍면동 코드', right_on='dong', how='left')

# 'dong' 컬럼 제거 후 원하는 컬럼 순서로 재정리
df = df[['읍면동 코드', '인구수', 'adm_cd']]

# adm_cd 컬럼에 NaN이 있는 행 제거
df = df.dropna(subset=['adm_cd'])

# 7. Choropleth에서 사용할 key 컬럼 'adm_cd'는 반드시 숫자형이어야 함
df['adm_cd'] = pd.to_numeric(df['adm_cd'], errors='coerce')

print(df.head())

  읍면동 코드   인구수     adm_cd
2    동인동  8465  2201070.0
3    삼덕동  6739  2201054.0
4   성내1동  4866  2201056.0
5   성내2동  7003  2201059.0
6   성내3동  9540  2201061.0


##choropleth

In [ ]:
!pip install geopandas

In [ ]:
import geopandas as gpd

In [ ]:
dg_geo = gpd.read_file('/content/hangjeongdong_대구광역시.geojson')
dg_geo

OBJECTID         adm_nm   adm_cd     adm_cd2    sgg sido sidonm sggnm  \
0         625   대구광역시 중구 삼덕동  2201054  2711054500  27110   27  대구광역시    중구   
1         626  대구광역시 중구 성내1동  2201056  2711056500  27110   27  대구광역시    중구   
2         627  대구광역시 중구 성내2동  2201059  2711057500  27110   27  대구광역시    중구   
3         628  대구광역시 중구 성내3동  2201061  2711058500  27110   27  대구광역시    중구   
4         629   대구광역시 중구 대신동  2201062  2711059500  27110   27  대구광역시    중구   
..        ...            ...      ...         ...    ...  ...    ...   ...   
136       761  대구광역시 달성군 현풍읍  2231016  2771026500  27710   27  대구광역시   달성군   
137       762  대구광역시 달성군 유가읍  2231014  2771025900  27710   27  대구광역시   달성군   
138       763  대구광역시 달성군 구지면  2231036  2771038000  27710   27  대구광역시   달성군   
139      3489  대구광역시 동구 안심3동  2202076  2714074200  27140   27  대구광역시    동구   
140      3490   대구광역시 동구 혁신동  2202078  2714075500  27140   27  대구광역시    동구   

                                              geometry  
0    MULTIPOLYGON (((128.59981 35.86827, 128.60252 ...  
1    MULTIPOLYGON (((128.60136 35.8748, 128.59981 3...  
2    MULTIPOLYGON (((128.59495 35.8753, 128.59407 3...  
3    MULTIPOLYGON (((128.58017 35.87908, 128.58838 ...  
4    MULTIPOLYGON (((128.58261 35.87059, 128.58235 ...  
..                                                 ...  
136  MULTIPOLYGON (((128.4571 35.7156, 128.45764 35...  
137  MULTIPOLYGON (((128.52314 35.71888, 128.52337 ...  
138  MULTIPOLYGON (((128.37517 35.70249, 128.37478 ...  
139  MULTIPOLYGON (((128.73427 35.87484, 128.73604 ...  
140  MULTIPOLYGON (((128.73427 35.87484, 128.72756 ...  

[141 rows x 9 columns]

In [ ]:
# geojson 데이터 준비
with open('/content/hangjeongdong_대구광역시.geojson', mode='r', encoding='utf-8') as f:
    geo = json.loads(f.read())

# 심인중학교(대구)를 중심으로 지도 생성
loc = (35.8714354, 128.601445)
m = folium.Map(location=loc, zoom_start=11)

# choropleth 시각화 (여기서는 'adm_cd'와 '인구수' 컬럼을 사용)
folium.Choropleth(
    geo_data=geo,
    data=df,
    columns=['adm_cd', '인구수'],
    key_on='properties.adm_cd',
    legend_name='읍면동별 인구수',
    fill_color='YlOrRd',
    fill_opacity=0.5,
    line_opacity=0.5
).add_to(m)

# 스타일 및 tooltip 설정
style_function = lambda x: {
    'fillColor': '#ffffff',
    'color': '#000000',
    'fillOpacity': 0.1,
    'weight': 0.1
}
highlight_function = lambda x: {
    'fillColor': '#000000',
    'color': '#000000',
    'fillOpacity': 0.50,
    'weight': 0.1
}

# 여기서는 geopandas로 읽어들인 dg_geo를 사용 (이미 dg_geo는 준비되었다고 가정)
NIL = folium.features.GeoJson(
    dg_geo,
    style_function=style_function,
    control=False,
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
        fields=['adm_nm'],
        aliases=['동이름: '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")
    )
)
m.add_child(NIL)
m.keep_in_front(NIL)

m

#**Traffic Volume by District**

In [ ]:
import pandas as pd

In [ ]:
# 파일을 읽어 데이터프레임으로 변환

df_a = pd.read_csv('/content/첨두시_교차로.csv', encoding='utf-8')
df_b = pd.read_csv('/content/첨두시_교통량.csv', encoding='utf-8')

In [ ]:
merged_df = pd.concat([df_a, df_b], ignore_index=True)
print(merged_df)

      구분      조사지점명 교통량(대/6시간) 첨두시 교통량(대/시)  첨두율(%)  차로수\n(왕복) 교통량\n(대/24시간)  \
0    교차로      중앙네거리     13,474        2,712   20.13        NaN           NaN   
1    교차로     대구역네거리     20,462        4,160   20.33        NaN           NaN   
2    교차로     반월당네거리     35,645        7,222   20.26        NaN           NaN   
3    교차로      공고네거리     22,897        4,399   19.21        NaN           NaN   
4    교차로    동대구역네거리     35,915        6,637   18.48        NaN           NaN   
..   ...        ...        ...          ...     ...        ...           ...   
154  교차로    설화명곡네거리        NaN          NaN     NaN        NaN           NaN   
155  교차로  박석진교동측네거리        NaN          NaN     NaN        NaN           NaN   
156  교차로   휴양림입구네거리        NaN          NaN     NaN        NaN           NaN   
157  교차로      차천네거리        NaN          NaN     NaN        NaN           NaN   
158  교차로         전체        NaN          NaN     NaN        NaN           NaN   

    (대/시) (대/시/차로당)  첨두율\n(%)  
0     N

In [ ]:
import pandas as pd

output_file_path = 'merged_data.csv'
merged_df.to_csv(output_file_path, encoding='cp949', index=False)

print(f"데이터가 {output_file_path}에 성공적으로 저장되었습니다.")

데이터가 merged_data.csv에 성공적으로 저장되었습니다.


In [ ]:
df_traffic= pd.read_csv('교통량_lonlat.csv', encoding='cp949')
df_traffic

구분    조사지점명  교통량(대/6시간)  교통량(대/시)  첨두율(%)  차로수\n(왕복) 교통량\n(대/24시간)  \
0    교차로    중앙네거리     13474.0    2712.0   20.13        NaN           NaN   
1    교차로   대구역네거리     20462.0    4160.0   20.33        NaN           NaN   
2    교차로   반월당네거리     35645.0    7222.0   20.26        NaN           NaN   
3    교차로    공고네거리     22897.0    4399.0   19.21        NaN           NaN   
4    교차로  동대구역네거리     35915.0    6637.0   18.48        NaN           NaN   
..   ...      ...         ...       ...     ...        ...           ...   
80  간선도로   달구벌대로2    198776.0    5152.0   10.37       10.0        49,694   
81  간선도로      청호로     65304.0    1762.0   10.79        6.0        16,326   
82  간선도로  테크노폴리스로    120640.0    3140.0   10.41        4.0        30,160   
83  간선도로    앞산터널로    128196.0    4008.0   12.51        6.0        32,049   
84   NaN      NaN         NaN       NaN     NaN        NaN           NaN   

   (대/시/차로당)        lat         lon  Unnamed: 10  
0        NaN  35.871158  128.593978          NaN  
1        NaN  35.875109  128.594821          NaN  
2        NaN  35.865623  128.593399          NaN  
3        NaN  35.881303  128.614173          NaN  
4        NaN  35.876797  128.626149          NaN  
..       ...        ...         ...          ...  
80       515  35.863865  128.591535          NaN  
81       294  35.840620  128.644304          NaN  
82       785  35.693611  128.460114          NaN  
83       668  35.807096  128.563433          NaN  
84       NaN        NaN         NaN          NaN  

[85 rows x 11 columns]

In [ ]:
df_traffic_sp=df_traffic[['구분','조사지점명','교통량(대/시)','첨두율(%)','lon','lat']]
df_traffic_sp=df_traffic_sp[:84]
df_traffic_sp

구분    조사지점명  교통량(대/시)  첨두율(%)         lon        lat
0    교차로    중앙네거리    2712.0   20.13  128.593978  35.871158
1    교차로   대구역네거리    4160.0   20.33  128.594821  35.875109
2    교차로   반월당네거리    7222.0   20.26  128.593399  35.865623
3    교차로    공고네거리    4399.0   19.21  128.614173  35.881303
4    교차로  동대구역네거리    6637.0   18.48  128.626149  35.876797
..   ...      ...       ...     ...         ...        ...
79  간선도로      파동로    1236.0    8.62  128.615968  35.815739
80  간선도로   달구벌대로2    5152.0   10.37  128.591535  35.863865
81  간선도로      청호로    1762.0   10.79  128.644304  35.840620
82  간선도로  테크노폴리스로    3140.0   10.41  128.460114  35.693611
83  간선도로    앞산터널로    4008.0   12.51  128.563433  35.807096

[84 rows x 6 columns]

In [ ]:
sampling_traffic=df_traffic_sp[df_traffic_sp['첨두율(%)']<20]
sampling_traffic

구분    조사지점명  교통량(대/시)  첨두율(%)         lon        lat
3    교차로    공고네거리    4399.0   19.21  128.614173  35.881303
4    교차로  동대구역네거리    6637.0   18.48  128.626149  35.876797
5    교차로    범어네거리   11871.0   18.77  128.626214  35.859152
6    교차로    명덕네거리    4604.0   19.35  128.590694  35.856999
7    교차로   반고개네거리    7481.0   19.80  128.574404  35.860033
..   ...      ...       ...     ...         ...        ...
79  간선도로      파동로    1236.0    8.62  128.615968  35.815739
80  간선도로   달구벌대로2    5152.0   10.37  128.591535  35.863865
81  간선도로      청호로    1762.0   10.79  128.644304  35.840620
82  간선도로  테크노폴리스로    3140.0   10.41  128.460114  35.693611
83  간선도로    앞산터널로    4008.0   12.51  128.563433  35.807096

[74 rows x 6 columns]

In [ ]:
df_traffic_sort=sampling_traffic.sort_values(by=['교통량(대/시)','첨두율(%)'], ascending=[False, True])
df_traffic_sort

구분      조사지점명  교통량(대/시)  첨두율(%)         lon        lat
5    교차로      범어네거리   11871.0   18.77  128.626214  35.859152
13   교차로      효목네거리   10322.0   19.71  128.644942  35.876749
12   교차로     큰고개오거리    9682.0   19.90  128.632901  35.885771
33   교차로      죽전네거리    9391.0   18.41  128.537193  35.850219
19   교차로      두류네거리    8879.0   19.26  128.557445  35.858013
..   ...        ...       ...     ...         ...        ...
28   교차로     수성못오거리    1815.0   17.26  128.609826  35.825473
36   교차로  더샵1차북편삼거리    1798.0   17.10  128.641158  35.926928
81  간선도로        청호로    1762.0   10.79  128.644304  35.840620
79  간선도로        파동로    1236.0    8.62  128.615968  35.815739
49    교량        조야교    1119.0   10.92  128.578294  35.906084

[74 rows x 6 columns]

In [ ]:
rank_traffic15=df_traffic_sort.head(15)
rank_traffic15

구분    조사지점명  교통량(대/시)  첨두율(%)         lon        lat
5    교차로    범어네거리   11871.0   18.77  128.626214  35.859152
13   교차로    효목네거리   10322.0   19.71  128.644942  35.876749
12   교차로   큰고개오거리    9682.0   19.90  128.632901  35.885771
33   교차로    죽전네거리    9391.0   18.41  128.537193  35.850219
19   교차로    두류네거리    8879.0   19.26  128.557445  35.858013
14   교차로    만촌네거리    7861.0   18.20  128.646124  35.859043
11   교차로    복현오거리    7817.0   18.55  128.614983  35.897674
7    교차로   반고개네거리    7481.0   19.80  128.574404  35.860033
29   교차로    상인네거리    7245.0   18.03  128.537965  35.819144
15   교차로    황금네거리    7195.0   19.10  128.623999  35.839933
64  간선도로     신천대로    6820.0    9.17  128.615215  35.809755
24   교차로   반야월삼거리    6786.0   18.69  128.688226  35.874488
48    교량      팔달교    6780.0    7.43  128.550803  35.895143
30   교차로    본리네거리    6727.0   18.02  128.537059  35.837623
4    교차로  동대구역네거리    6637.0   18.48  128.626149  35.876797

In [ ]:
score_list = [i+1 for i in range(len(rank_traffic15))]
score_list

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15]

In [ ]:
score_list = score_list[::-1]
score_list

[15, 14, 13, 12, 11, 10, 9, 8, 7, 6, 5, 4, 3, 2, 1]

In [ ]:
rank_traffic15


구분    조사지점명  교통량(대/시)  첨두율(%)         lon        lat
5    교차로    범어네거리   11871.0   18.77  128.626214  35.859152
13   교차로    효목네거리   10322.0   19.71  128.644942  35.876749
12   교차로   큰고개오거리    9682.0   19.90  128.632901  35.885771
33   교차로    죽전네거리    9391.0   18.41  128.537193  35.850219
19   교차로    두류네거리    8879.0   19.26  128.557445  35.858013
14   교차로    만촌네거리    7861.0   18.20  128.646124  35.859043
11   교차로    복현오거리    7817.0   18.55  128.614983  35.897674
7    교차로   반고개네거리    7481.0   19.80  128.574404  35.860033
29   교차로    상인네거리    7245.0   18.03  128.537965  35.819144
15   교차로    황금네거리    7195.0   19.10  128.623999  35.839933
64  간선도로     신천대로    6820.0    9.17  128.615215  35.809755
24   교차로   반야월삼거리    6786.0   18.69  128.688226  35.874488
48    교량      팔달교    6780.0    7.43  128.550803  35.895143
30   교차로    본리네거리    6727.0   18.02  128.537059  35.837623
4    교차로  동대구역네거리    6637.0   18.48  128.626149  35.876797

In [ ]:
rank_traffic15.to_csv('rank_traffic15.csv', encoding='cp949', index=False)

#**Vehicle-to-Charging Station Ratio**

In [ ]:
import pandas as pd
import numpy as np
import geopandas as gpd
from tqdm import tqdm
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon
import folium
import seaborn as sns
from patsy import dmatrices
import statsmodels.api as sm;
from statsmodels.stats.outliers_influence import variance_inflation_factor
%matplotlib inline
from patsy import dmatrix
import json

In [ ]:
#전기차 충전기 구축 현황 파일
df_rid = pd.read_csv('/content/대구광역시_전기차 충전기 구축 현황_20240116.csv', encoding='cp949')
df_rid.head(3)

충전소명                                                주소  ID  \
0   DTC섬유박물관              대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)   1   
1  갓바위공영3주차장  대구광역시 동구 갓바위로 227갓바위공영3주차장(진인동 123-74 갓바위공영3주차장)   1   
2  갓바위공영3주차장  대구광역시 동구 갓바위로 227갓바위공영3주차장(진인동 123-74 갓바위공영3주차장)   2   

            충전기 형태 충전기 용량  
0  DC차데모+AC3상+DC콤보   50kW  
1             AC완속    7kW  
2             AC완속    7kW

##전처리

In [ ]:
#자료형 확인
df_rid.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 321 entries, 0 to 320
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   충전소명    321 non-null    object
 1   주소      321 non-null    object
 2   ID      321 non-null    int64 
 3   충전기 형태  321 non-null    object
 4   충전기 용량  320 non-null    object
dtypes: int64(1), object(4)
memory usage: 12.7+ KB


In [ ]:
#결측치 확인
df_rid.isna().sum()

충전소명      0
주소        0
ID        0
충전기 형태    0
충전기 용량    1
dtype: int64

In [ ]:
df_rid[df_rid['충전기 용량'].isna()]

충전소명                                          주소  ID           충전기 형태  \
133  명복공원주차장  대구광역시 수성구 달구벌대로541길 47명복공원 주차장(고모동 산113-3)   1  DC차데모+AC3상+DC콤보   

    충전기 용량  
133    NaN

결측치 하나 밖에 없어 찾아본 결과, 명복공원주차장은 충전기 용량은 50kW로 확인

∴ 결측치는 50kW로 채우기

In [ ]:
df_rid = df_rid.fillna('50kW')

In [ ]:
# 명복공원주차장 확인
df_rid.loc[[133]]

충전소명                                          주소  ID           충전기 형태  \
133  명복공원주차장  대구광역시 수성구 달구벌대로541길 47명복공원 주차장(고모동 산113-3)   1  DC차데모+AC3상+DC콤보   

    충전기 용량  
133   50kW

In [ ]:
df_rid['충전기 형태'].unique()

array(['DC차데모+AC3상+DC콤보', 'AC완속', 'DC콤보'], dtype=object)

In [ ]:
df_rid[['충전기 형태', '충전기 용량']].drop_duplicates()

충전기 형태 충전기 용량
0    DC차데모+AC3상+DC콤보   50kW
1               AC완속    7kW
168  DC차데모+AC3상+DC콤보   50KW
228  DC차데모+AC3상+DC콤보  100kW
291             AC완속    7KW
292             DC콤보  100kW
301  DC차데모+AC3상+DC콤보  100KW

kW / KW 같은 단위이므로 kW로 통일시켜주기

In [ ]:
df_rid['충전기 용량'] = df_rid['충전기 용량'].str.replace('KW', 'kW')

In [ ]:
# 잘 변경되었는지 확인
df_rid[['충전기 형태', '충전기 용량']].drop_duplicates()

충전기 형태 충전기 용량
0    DC차데모+AC3상+DC콤보   50kW
1               AC완속    7kW
228  DC차데모+AC3상+DC콤보  100kW
292             DC콤보  100kW

In [ ]:
#전기차 충전기 이용현황
df_use = pd.read_csv('/content/대구광역시_전기자동차 충전기 이용 현황_20230831.csv', encoding = 'cp949', parse_dates=['일자'])
df_use.head(2)

<ipython-input-56-cbf1a584430e>:2: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df_use = pd.read_csv('/content/대구광역시_전기자동차 충전기 이용 현황_20230831.csv', encoding = 'cp949', parse_dates=['일자'])


일자     충전소ID      충전소명칭        위도          경도  충전기ID 충전기타입  사용횟수  \
0 2023-08-31  27140008   DTC섬유박물관  35.91898  128.639976      1    급속     2   
1 2023-08-31  27290051  가창면행정복지센터  35.80279  128.622560      1    완속     2   

     충전량  
0  40.16  
1  48.36

In [ ]:
#자료형 확인
df_use.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 396159 entries, 0 to 396158
Data columns (total 9 columns):
 #   Column  Non-Null Count   Dtype         
---  ------  --------------   -----         
 0   일자      396159 non-null  datetime64[ns]
 1   충전소ID   396159 non-null  object        
 2   충전소명칭   396159 non-null  object        
 3   위도      396159 non-null  float64       
 4   경도      396159 non-null  float64       
 5   충전기ID   396159 non-null  int64         
 6   충전기타입   396159 non-null  object        
 7   사용횟수    396159 non-null  int64         
 8   충전량     396158 non-null  float64       
dtypes: datetime64[ns](1), float64(3), int64(2), object(3)
memory usage: 27.2+ MB


In [ ]:
#결측치 확인
df_use.isna().sum()

일자       0
충전소ID    0
충전소명칭    0
위도       0
경도       0
충전기ID    0
충전기타입    0
사용횟수     0
충전량      1
dtype: int64

In [ ]:
df_use[df_use['충전량'].isna()]

일자     충전소ID       충전소명칭        위도          경도  충전기ID 충전기타입  \
105996 2022-05-10  DGMS0001  대구시_명성푸르지오  35.88899  128.589744      3    완속   

        사용횟수  충전량  
105996     1  NaN

이 결측치 어떻게 처리하면 좋을지?

1. 대구시 명성푸르지오의 충전기 id가 3, 사용횟수가 1인 충전량을 다 뽑아 평균을 넣는다
2. 396159개의 데이터 중 하나이므로 제거한다

=> 1번 결정

In [ ]:
df_rid[df_rid['충전소명'] == '대구시_명성푸르지오']

충전소명                주소  ID           충전기 형태 충전기 용량
188  대구시_명성푸르지오  대구광역시 북구 침산로 153   1  DC차데모+AC3상+DC콤보   50kW
189  대구시_명성푸르지오  대구광역시 북구 침산로 153   2             AC완속    7kW
190  대구시_명성푸르지오  대구광역시 북구 침산로 153   3             AC완속    7kW

In [ ]:
df_use.fillna(round(df_use[(df_use['충전소명칭'] == '대구시_명성푸르지오') & (df_use['충전기ID'] == 3) & df_use['사용횟수'] == 1]['충전량'].mean(), 2), inplace=True)

In [ ]:
df_use.loc[[105996]]

일자     충전소ID       충전소명칭        위도          경도  충전기ID 충전기타입  \
105996 2022-05-10  DGMS0001  대구시_명성푸르지오  35.88899  128.589744      3    완속   

        사용횟수    충전량  
105996     1  32.86

In [ ]:
df_use[(df_use['충전소명칭'] == '대구시_명성푸르지오') & (df_use['충전기ID'] == 3)]['충전량'].mean()

36.74474929145935

In [ ]:
#데이터 확인
len(df_use['충전소명칭'].unique())

223

In [ ]:
len(df_rid['충전소명'].unique())

217

위도&경도는 충전소 명칭-충전기ID & 충전소명-ID 두 개 열을 가지고 left join 해주기

In [ ]:
df_rid.head(1)

충전소명                                    주소  ID           충전기 형태 충전기 용량
0  DTC섬유박물관  대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)   1  DC차데모+AC3상+DC콤보   50kW

In [ ]:
# 2023년 제외 나머지 제거
df_use

일자     충전소ID      충전소명칭        위도          경도  충전기ID 충전기타입  \
0      2023-08-31  27140008   DTC섬유박물관  35.91898  128.639976      1    급속   
1      2023-08-31  27290051  가창면행정복지센터  35.80279  128.622560      1    완속   
2      2023-08-31  27140001  갓바위공영3주차장  35.97027  128.725839      1    완속   
3      2023-08-31  27140002  갓바위공영5주차장  35.96938  128.726065      1    급속   
4      2023-08-31  27230039  검단동행정복지센터  35.91342  128.627216      1    완속   
...           ...       ...        ...       ...         ...    ...   ...   
396154 2018-01-01  27710002       달성군청  35.77387  128.430902      2    완속   
396155 2018-01-01  27710003      대구과학관  35.68520  128.465865      1    급속   
396156 2018-01-01  27710003      대구과학관  35.68520  128.465865      2    완속   
396157 2018-01-01  27710003      대구과학관  35.68520  128.465865      3    완속   
396158 2018-01-01  27710003      대구과학관  35.68520  128.465865      4    완속   

        사용횟수     충전량  
0          2   40.16  
1          2   48.36  
2          1    1.09  
3          1   10.17  
4          3   42.05  
...      ...     ...  
396154     2    0.31  
396155     8  130.96  
396156     1    2.92  
396157     3   28.24  
396158     2   47.96  

[396159 rows x 9 columns]

In [ ]:
df_use['year'] = df_use['일자'].dt.year
df_use['month'] = df_use['일자'].dt.month
df_use['day'] = df_use['일자'].dt.day
df_use['dayname'] = df_use['일자'].dt.day_name()
df_use.head(1)

일자     충전소ID     충전소명칭        위도          경도  충전기ID 충전기타입  사용횟수  \
0 2023-08-31  27140008  DTC섬유박물관  35.91898  128.639976      1    급속     2   

     충전량  year  month  day   dayname  
0  40.16  2023      8   31  Thursday

In [ ]:
df_use_2023 = df_use[df_use['year'] == 2023]
df_use_2023

일자     충전소ID             충전소명칭        위도          경도  충전기ID  \
0     2023-08-31  27140008          DTC섬유박물관  35.91898  128.639976      1   
1     2023-08-31  27290051         가창면행정복지센터  35.80279  128.622560      1   
2     2023-08-31  27140001         갓바위공영3주차장  35.97027  128.725839      1   
3     2023-08-31  27140002         갓바위공영5주차장  35.96938  128.726065      1   
4     2023-08-31  27230039         검단동행정복지센터  35.91342  128.627216      1   
...          ...       ...               ...       ...         ...    ...   
50991 2023-01-01  HGDR0001  대구시_한국도로공사(유천IC)  35.81086  128.501556      1   
50992 2023-01-01  HGDR0001  대구시_한국도로공사(유천IC)  35.81086  128.501556      2   
50993 2023-01-01  DGHG0001   대구시_황금1동 행정복지센터  35.84398  128.638144      1   
50994 2023-01-01  DGHM0001   대구시_효목1동 행정복지센터  35.88186  128.644950      1   
50995 2023-01-01  DGHH0001          대구시_효목2동  35.87814  128.641241      1   

      충전기타입  사용횟수         충전량  year  month  day   dayname  
0        급속     2   40.160000  2023      8   31  Thursday  
1        완속     2   48.360000  2023      8   31  Thursday  
2        완속     1    1.090000  2023      8   31  Thursday  
3        급속     1   10.170000  2023      8   31  Thursday  
4        완속     3   42.050000  2023      8   31  Thursday  
...     ...   ...         ...   ...    ...  ...       ...  
50991    급속     2   61.870001  2023      1    1    Sunday  
50992    급속     3   96.830000  2023      1    1    Sunday  
50993    급속     7  169.139999  2023      1    1    Sunday  
50994    급속     7  131.759999  2023      1    1    Sunday  
50995    급속    10  173.110000  2023      1    1    Sunday  

[50996 rows x 13 columns]

In [ ]:
# df_rid & df_use join
df_rid.head(1)

충전소명                                    주소  ID           충전기 형태 충전기 용량
0  DTC섬유박물관  대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)   1  DC차데모+AC3상+DC콤보   50kW

In [ ]:
df_use_2023.head(1)

일자     충전소ID     충전소명칭        위도          경도  충전기ID 충전기타입  사용횟수  \
0 2023-08-31  27140008  DTC섬유박물관  35.91898  128.639976      1    급속     2   

     충전량  year  month  day   dayname  
0  40.16  2023      8   31  Thursday

In [ ]:
# 열 이름 동일하게 변경
df_rid.rename(columns={'충전소명':'충전소명칭', 'ID':'충전기ID'}, inplace=True)
df_rid.head(1)

충전소명칭                                    주소  충전기ID           충전기 형태  \
0  DTC섬유박물관  대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)      1  DC차데모+AC3상+DC콤보   

  충전기 용량  
0   50kW

In [ ]:
df_all = pd.merge(df_use_2023, df_rid, how='left', on=['충전소명칭', '충전기ID'])
df_all

일자     충전소ID             충전소명칭        위도          경도  충전기ID  \
0     2023-08-31  27140008          DTC섬유박물관  35.91898  128.639976      1   
1     2023-08-31  27290051         가창면행정복지센터  35.80279  128.622560      1   
2     2023-08-31  27140001         갓바위공영3주차장  35.97027  128.725839      1   
3     2023-08-31  27140002         갓바위공영5주차장  35.96938  128.726065      1   
4     2023-08-31  27230039         검단동행정복지센터  35.91342  128.627216      1   
...          ...       ...               ...       ...         ...    ...   
50991 2023-01-01  HGDR0001  대구시_한국도로공사(유천IC)  35.81086  128.501556      1   
50992 2023-01-01  HGDR0001  대구시_한국도로공사(유천IC)  35.81086  128.501556      2   
50993 2023-01-01  DGHG0001   대구시_황금1동 행정복지센터  35.84398  128.638144      1   
50994 2023-01-01  DGHM0001   대구시_효목1동 행정복지센터  35.88186  128.644950      1   
50995 2023-01-01  DGHH0001          대구시_효목2동  35.87814  128.641241      1   

      충전기타입  사용횟수         충전량  year  month  day   dayname  \
0        급속     2   40.160000  2023      8   31  Thursday   
1        완속     2   48.360000  2023      8   31  Thursday   
2        완속     1    1.090000  2023      8   31  Thursday   
3        급속     1   10.170000  2023      8   31  Thursday   
4        완속     3   42.050000  2023      8   31  Thursday   
...     ...   ...         ...   ...    ...  ...       ...   
50991    급속     2   61.870001  2023      1    1    Sunday   
50992    급속     3   96.830000  2023      1    1    Sunday   
50993    급속     7  169.139999  2023      1    1    Sunday   
50994    급속     7  131.759999  2023      1    1    Sunday   
50995    급속    10  173.110000  2023      1    1    Sunday   

                                                      주소           충전기 형태  \
0                   대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)  DC차데모+AC3상+DC콤보   
1             대구광역시 달성군 가창면 가창로 1100가창면행정복지센터(82 가창면사무소)             AC완속   
2       대구광역시 동구 갓바위로 227갓바위공영3주차장(진인동 123-74 갓바위공영3주차장)             AC완속   
3      대구광역시 동구 갓바위로 223-35갓바위공영5주차장(진인동 123-12 갓바위공영...  DC차데모+AC3상+DC콤보   
4                대구광역시 북구 검단로41길 12검단동행정복지센터(검단동 행정복지센터)             AC완속   
...                                                  ...              ...   
50991                  대구광역시 달성군 화원읍 성천로 208한국도로공사(유천IC)  DC차데모+AC3상+DC콤보   
50992                  대구광역시 달성군 화원읍 성천로 208한국도로공사(유천IC)  DC차데모+AC3상+DC콤보   
50993                                                NaN              NaN   
50994                                                NaN              NaN   
50995                         대구광역시 동구 화랑로25길 45대구시_효목2동  DC차데모+AC3상+DC콤보   

      충전기 용량  
0       50kW  
1        7kW  
2        7kW  
3       50kW  
4        7kW  
...      ...  
50991   50kW  
50992   50kW  
50993    NaN  
50994    NaN  
50995  100kW  

[50996 rows x 16 columns]

In [ ]:
df_all.isna().sum()

일자             0
충전소ID          0
충전소명칭          0
위도             0
경도             0
충전기ID          0
충전기타입          0
사용횟수           0
충전량            0
year           0
month          0
day            0
dayname        0
주소         20692
충전기 형태     20692
충전기 용량     20692
dtype: int64

결측치는 충전소 개수 6개에 대한 차이로 보임 -> 논의 후 결측치 제거

In [ ]:
df_all.to_csv('alldata.csv', index=False, encoding='cp949')

##충전소 데이터

In [ ]:
df_cs = pd.read_csv('/content/alldata.csv', encoding='cp949')
df_cs.head(3)

일자     충전소ID      충전소명칭        위도          경도  충전기ID 충전기타입  사용횟수  \
0  2023-08-31  27140008   DTC섬유박물관  35.91898  128.639976      1    급속     2   
1  2023-08-31  27290051  가창면행정복지센터  35.80279  128.622560      1    완속     2   
2  2023-08-31  27140001  갓바위공영3주차장  35.97027  128.725839      1    완속     1   

     충전량  year  month  day   dayname  \
0  40.16  2023      8   31  Thursday   
1  48.36  2023      8   31  Thursday   
2   1.09  2023      8   31  Thursday   

                                                 주소           충전기 형태 충전기 용량  
0              대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)  DC차데모+AC3상+DC콤보   50kW  
1        대구광역시 달성군 가창면 가창로 1100가창면행정복지센터(82 가창면사무소)             AC완속    7kW  
2  대구광역시 동구 갓바위로 227갓바위공영3주차장(진인동 123-74 갓바위공영3주차장)             AC완속    7kW

##geojson 파일

In [ ]:
#파일 불러오기
dg_geo = gpd.read_file('/content/hangjeongdong_대구광역시.geojson')
dg_geo

OBJECTID         adm_nm   adm_cd     adm_cd2    sgg sido sidonm sggnm  \
0         625   대구광역시 중구 삼덕동  2201054  2711054500  27110   27  대구광역시    중구   
1         626  대구광역시 중구 성내1동  2201056  2711056500  27110   27  대구광역시    중구   
2         627  대구광역시 중구 성내2동  2201059  2711057500  27110   27  대구광역시    중구   
3         628  대구광역시 중구 성내3동  2201061  2711058500  27110   27  대구광역시    중구   
4         629   대구광역시 중구 대신동  2201062  2711059500  27110   27  대구광역시    중구   
..        ...            ...      ...         ...    ...  ...    ...   ...   
136       761  대구광역시 달성군 현풍읍  2231016  2771026500  27710   27  대구광역시   달성군   
137       762  대구광역시 달성군 유가읍  2231014  2771025900  27710   27  대구광역시   달성군   
138       763  대구광역시 달성군 구지면  2231036  2771038000  27710   27  대구광역시   달성군   
139      3489  대구광역시 동구 안심3동  2202076  2714074200  27140   27  대구광역시    동구   
140      3490   대구광역시 동구 혁신동  2202078  2714075500  27140   27  대구광역시    동구   

                                              geometry  
0    MULTIPOLYGON (((128.59981 35.86827, 128.60252 ...  
1    MULTIPOLYGON (((128.60136 35.8748, 128.59981 3...  
2    MULTIPOLYGON (((128.59495 35.8753, 128.59407 3...  
3    MULTIPOLYGON (((128.58017 35.87908, 128.58838 ...  
4    MULTIPOLYGON (((128.58261 35.87059, 128.58235 ...  
..                                                 ...  
136  MULTIPOLYGON (((128.4571 35.7156, 128.45764 35...  
137  MULTIPOLYGON (((128.52314 35.71888, 128.52337 ...  
138  MULTIPOLYGON (((128.37517 35.70249, 128.37478 ...  
139  MULTIPOLYGON (((128.73427 35.87484, 128.73604 ...  
140  MULTIPOLYGON (((128.73427 35.87484, 128.72756 ...  

[141 rows x 9 columns]

In [ ]:
dg_geo['geometry']

0      MULTIPOLYGON (((128.59981 35.86827, 128.60252 ...
1      MULTIPOLYGON (((128.60136 35.8748, 128.59981 3...
2      MULTIPOLYGON (((128.59495 35.8753, 128.59407 3...
3      MULTIPOLYGON (((128.58017 35.87908, 128.58838 ...
4      MULTIPOLYGON (((128.58261 35.87059, 128.58235 ...
                             ...                        
136    MULTIPOLYGON (((128.4571 35.7156, 128.45764 35...
137    MULTIPOLYGON (((128.52314 35.71888, 128.52337 ...
138    MULTIPOLYGON (((128.37517 35.70249, 128.37478 ...
139    MULTIPOLYGON (((128.73427 35.87484, 128.73604 ...
140    MULTIPOLYGON (((128.73427 35.87484, 128.72756 ...
Name: geometry, Length: 141, dtype: geometry

In [ ]:
#주차장 위경도가 어느 행정동에 포함되는
def find_admin_area(point, admin_areas):
    for index, row in admin_areas.iterrows():
        if row['geometry'].contains(point):
            return row['adm_nm']
    return None

In [ ]:
df_cs['geometry'] = [Point(xy) for xy in zip(df_cs['경도'], df_cs['위도'])]
df_cs.head(1)

일자     충전소ID     충전소명칭        위도          경도  충전기ID 충전기타입  사용횟수  \
0  2023-08-31  27140008  DTC섬유박물관  35.91898  128.639976      1    급속     2   

     충전량  year  month  day   dayname                                    주소  \
0  40.16  2023      8   31  Thursday  대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)   

            충전기 형태 충전기 용량                     geometry  
0  DC차데모+AC3상+DC콤보   50kW  POINT (128.639976 35.91898)

In [ ]:
df_cs['adm_nm'] = df_cs['geometry'].apply(lambda x: find_admin_area(x, dg_geo))
df_cs.head(1)

일자     충전소ID     충전소명칭        위도          경도  충전기ID 충전기타입  사용횟수  \
0  2023-08-31  27140008  DTC섬유박물관  35.91898  128.639976      1    급속     2   

     충전량  year  month  day   dayname                                    주소  \
0  40.16  2023      8   31  Thursday  대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)   

            충전기 형태 충전기 용량                     geometry           adm_nm  
0  DC차데모+AC3상+DC콤보   50kW  POINT (128.639976 35.91898)  대구광역시 동구 불로·봉무동

In [ ]:
df_cs.isna().sum()

일자              0
충전소ID           0
충전소명칭           0
위도              0
경도              0
충전기ID           0
충전기타입           0
사용횟수            0
충전량             0
year            0
month           0
day             0
dayname         0
주소          20692
충전기 형태      20692
충전기 용량      20692
geometry        0
adm_nm        103
dtype: int64

In [ ]:
df_cs.shape

(50996, 18)

In [ ]:
df_cs.dropna(subset=['adm_nm'], inplace=True)

In [ ]:
#읍면동 코드 데이터
#adm_cd와 동을 join
df_cs['gudong'] = df_cs['adm_nm'].str.replace('대구광역시 ', '')
df_cs

일자     충전소ID             충전소명칭        위도          경도  충전기ID  \
0      2023-08-31  27140008          DTC섬유박물관  35.91898  128.639976      1   
1      2023-08-31  27290051         가창면행정복지센터  35.80279  128.622560      1   
2      2023-08-31  27140001         갓바위공영3주차장  35.97027  128.725839      1   
3      2023-08-31  27140002         갓바위공영5주차장  35.96938  128.726065      1   
4      2023-08-31  27230039         검단동행정복지센터  35.91342  128.627216      1   
...           ...       ...               ...       ...         ...    ...   
50991  2023-01-01  HGDR0001  대구시_한국도로공사(유천IC)  35.81086  128.501556      1   
50992  2023-01-01  HGDR0001  대구시_한국도로공사(유천IC)  35.81086  128.501556      2   
50993  2023-01-01  DGHG0001   대구시_황금1동 행정복지센터  35.84398  128.638144      1   
50994  2023-01-01  DGHM0001   대구시_효목1동 행정복지센터  35.88186  128.644950      1   
50995  2023-01-01  DGHH0001          대구시_효목2동  35.87814  128.641241      1   

      충전기타입  사용횟수         충전량  year  month  day   dayname  \
0        급속     2   40.160000  2023      8   31  Thursday   
1        완속     2   48.360000  2023      8   31  Thursday   
2        완속     1    1.090000  2023      8   31  Thursday   
3        급속     1   10.170000  2023      8   31  Thursday   
4        완속     3   42.050000  2023      8   31  Thursday   
...     ...   ...         ...   ...    ...  ...       ...   
50991    급속     2   61.870001  2023      1    1    Sunday   
50992    급속     3   96.830000  2023      1    1    Sunday   
50993    급속     7  169.139999  2023      1    1    Sunday   
50994    급속     7  131.759999  2023      1    1    Sunday   
50995    급속    10  173.110000  2023      1    1    Sunday   

                                                      주소           충전기 형태  \
0                   대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)  DC차데모+AC3상+DC콤보   
1             대구광역시 달성군 가창면 가창로 1100가창면행정복지센터(82 가창면사무소)             AC완속   
2       대구광역시 동구 갓바위로 227갓바위공영3주차장(진인동 123-74 갓바위공영3주차장)             AC완속   
3      대구광역시 동구 갓바위로 223-35갓바위공영5주차장(진인동 123-12 갓바위공영...  DC차데모+AC3상+DC콤보   
4                대구광역시 북구 검단로41길 12검단동행정복지센터(검단동 행정복지센터)             AC완속   
...                                                  ...              ...   
50991                  대구광역시 달성군 화원읍 성천로 208한국도로공사(유천IC)  DC차데모+AC3상+DC콤보   
50992                  대구광역시 달성군 화원읍 성천로 208한국도로공사(유천IC)  DC차데모+AC3상+DC콤보   
50993                                                NaN              NaN   
50994                                                NaN              NaN   
50995                         대구광역시 동구 화랑로25길 45대구시_효목2동  DC차데모+AC3상+DC콤보   

      충전기 용량                     geometry           adm_nm     gudong  
0       50kW  POINT (128.639976 35.91898)  대구광역시 동구 불로·봉무동  동구 불로·봉무동  
1        7kW   POINT (128.62256 35.80279)    대구광역시 달성군 가창면    달성군 가창면  
2        7kW  POINT (128.725839 35.97027)     대구광역시 동구 공산동     동구 공산동  
3       50kW  POINT (128.726065 35.96938)     대구광역시 동구 공산동     동구 공산동  
4        7kW  POINT (128.627216 35.91342)     대구광역시 북구 검단동     북구 검단동  
...      ...                          ...              ...        ...  
50991   50kW  POINT (128.501556 35.81086)    대구광역시 달성군 화원읍    달성군 화원읍  
50992   50kW  POINT (128.501556 35.81086)    대구광역시 달성군 화원읍    달성군 화원읍  
50993    NaN  POINT (128.638144 35.84398)   대구광역시 수성구 황금1동   수성구 황금1동  
50994    NaN   POINT (128.64495 35.88186)    대구광역시 동구 효목1동    동구 효목1동  
50995  100kW  POINT (128.641241 35.87814)    대구광역시 동구 효목2동    동구 효목2동  

[50893 rows x 19 columns]

In [ ]:
df_emd = pd.read_csv('/content/대구광역시_읍면동코드.csv', encoding='cp949')
df_emd

sido    ssg   gu     adm_cd  dong
0    대구광역시  22010   중구        NaN   NaN
1    대구광역시  22010   중구  2201054.0   삼덕동
2    대구광역시  22010   중구  2201056.0  성내1동
3    대구광역시  22010   중구  2201059.0  성내2동
4    대구광역시  22010   중구  2201061.0  성내3동
..     ...    ...  ...        ...   ...
144  대구광역시  22310  달성군  2231031.0   가창면
145  대구광역시  22310  달성군  2231032.0   하빈면
146  대구광역시  22310  달성군  2231015.0   옥포읍
147  대구광역시  22310  달성군  2231016.0   현풍읍
148  대구광역시  22310  달성군  2231036.0   구지면

[149 rows x 5 columns]

In [ ]:
df_emd['gudong'] = df_emd['gu'] + ' ' + df_emd['dong']
df_emd

sido    ssg   gu     adm_cd  dong   gudong
0    대구광역시  22010   중구        NaN   NaN      NaN
1    대구광역시  22010   중구  2201054.0   삼덕동   중구 삼덕동
2    대구광역시  22010   중구  2201056.0  성내1동  중구 성내1동
3    대구광역시  22010   중구  2201059.0  성내2동  중구 성내2동
4    대구광역시  22010   중구  2201061.0  성내3동  중구 성내3동
..     ...    ...  ...        ...   ...      ...
144  대구광역시  22310  달성군  2231031.0   가창면  달성군 가창면
145  대구광역시  22310  달성군  2231032.0   하빈면  달성군 하빈면
146  대구광역시  22310  달성군  2231015.0   옥포읍  달성군 옥포읍
147  대구광역시  22310  달성군  2231016.0   현풍읍  달성군 현풍읍
148  대구광역시  22310  달성군  2231036.0   구지면  달성군 구지면

[149 rows x 6 columns]

In [ ]:
df_emd2 = df_emd[['gudong', 'adm_cd']]
df_emd2

gudong     adm_cd
0        NaN        NaN
1     중구 삼덕동  2201054.0
2    중구 성내1동  2201056.0
3    중구 성내2동  2201059.0
4    중구 성내3동  2201061.0
..       ...        ...
144  달성군 가창면  2231031.0
145  달성군 하빈면  2231032.0
146  달성군 옥포읍  2231015.0
147  달성군 현풍읍  2231016.0
148  달성군 구지면  2231036.0

[149 rows x 2 columns]

In [ ]:
df_emd2.dropna(inplace=True)
df_emd2

<ipython-input-104-f3fe0bdebc66>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_emd2.dropna(inplace=True)


gudong     adm_cd
1     중구 삼덕동  2201054.0
2    중구 성내1동  2201056.0
3    중구 성내2동  2201059.0
4    중구 성내3동  2201061.0
5     중구 대신동  2201062.0
..       ...        ...
144  달성군 가창면  2231031.0
145  달성군 하빈면  2231032.0
146  달성군 옥포읍  2231015.0
147  달성군 현풍읍  2231016.0
148  달성군 구지면  2231036.0

[141 rows x 2 columns]

In [ ]:
df_emd2['adm_cd'] = df_emd2['adm_cd'].astype('int64')
df_emd2

<ipython-input-105-1baa3fcb732e>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_emd2['adm_cd'] = df_emd2['adm_cd'].astype('int64')


gudong   adm_cd
1     중구 삼덕동  2201054
2    중구 성내1동  2201056
3    중구 성내2동  2201059
4    중구 성내3동  2201061
5     중구 대신동  2201062
..       ...      ...
144  달성군 가창면  2231031
145  달성군 하빈면  2231032
146  달성군 옥포읍  2231015
147  달성군 현풍읍  2231016
148  달성군 구지면  2231036

[141 rows x 2 columns]

In [ ]:
#parking과 emd merge
df_cs.head(1)

일자     충전소ID     충전소명칭        위도          경도  충전기ID 충전기타입  사용횟수  \
0  2023-08-31  27140008  DTC섬유박물관  35.91898  128.639976      1    급속     2   

     충전량  year  month  day   dayname                                    주소  \
0  40.16  2023      8   31  Thursday  대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)   

            충전기 형태 충전기 용량                     geometry           adm_nm  \
0  DC차데모+AC3상+DC콤보   50kW  POINT (128.639976 35.91898)  대구광역시 동구 불로·봉무동   

      gudong  
0  동구 불로·봉무동

In [ ]:
alldata = pd.merge(df_cs, df_emd2, how='left', on='gudong')
alldata

일자     충전소ID             충전소명칭        위도          경도  충전기ID  \
0      2023-08-31  27140008          DTC섬유박물관  35.91898  128.639976      1   
1      2023-08-31  27290051         가창면행정복지센터  35.80279  128.622560      1   
2      2023-08-31  27140001         갓바위공영3주차장  35.97027  128.725839      1   
3      2023-08-31  27140002         갓바위공영5주차장  35.96938  128.726065      1   
4      2023-08-31  27230039         검단동행정복지센터  35.91342  128.627216      1   
...           ...       ...               ...       ...         ...    ...   
50888  2023-01-01  HGDR0001  대구시_한국도로공사(유천IC)  35.81086  128.501556      1   
50889  2023-01-01  HGDR0001  대구시_한국도로공사(유천IC)  35.81086  128.501556      2   
50890  2023-01-01  DGHG0001   대구시_황금1동 행정복지센터  35.84398  128.638144      1   
50891  2023-01-01  DGHM0001   대구시_효목1동 행정복지센터  35.88186  128.644950      1   
50892  2023-01-01  DGHH0001          대구시_효목2동  35.87814  128.641241      1   

      충전기타입  사용횟수         충전량  year  month  day   dayname  \
0        급속     2   40.160000  2023      8   31  Thursday   
1        완속     2   48.360000  2023      8   31  Thursday   
2        완속     1    1.090000  2023      8   31  Thursday   
3        급속     1   10.170000  2023      8   31  Thursday   
4        완속     3   42.050000  2023      8   31  Thursday   
...     ...   ...         ...   ...    ...  ...       ...   
50888    급속     2   61.870001  2023      1    1    Sunday   
50889    급속     3   96.830000  2023      1    1    Sunday   
50890    급속     7  169.139999  2023      1    1    Sunday   
50891    급속     7  131.759999  2023      1    1    Sunday   
50892    급속    10  173.110000  2023      1    1    Sunday   

                                                      주소           충전기 형태  \
0                   대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)  DC차데모+AC3상+DC콤보   
1             대구광역시 달성군 가창면 가창로 1100가창면행정복지센터(82 가창면사무소)             AC완속   
2       대구광역시 동구 갓바위로 227갓바위공영3주차장(진인동 123-74 갓바위공영3주차장)             AC완속   
3      대구광역시 동구 갓바위로 223-35갓바위공영5주차장(진인동 123-12 갓바위공영...  DC차데모+AC3상+DC콤보   
4                대구광역시 북구 검단로41길 12검단동행정복지센터(검단동 행정복지센터)             AC완속   
...                                                  ...              ...   
50888                  대구광역시 달성군 화원읍 성천로 208한국도로공사(유천IC)  DC차데모+AC3상+DC콤보   
50889                  대구광역시 달성군 화원읍 성천로 208한국도로공사(유천IC)  DC차데모+AC3상+DC콤보   
50890                                                NaN              NaN   
50891                                                NaN              NaN   
50892                         대구광역시 동구 화랑로25길 45대구시_효목2동  DC차데모+AC3상+DC콤보   

      충전기 용량                     geometry           adm_nm     gudong   adm_cd  
0       50kW  POINT (128.639976 35.91898)  대구광역시 동구 불로·봉무동  동구 불로·봉무동  2202063  
1        7kW   POINT (128.62256 35.80279)    대구광역시 달성군 가창면    달성군 가창면  2231031  
2        7kW  POINT (128.725839 35.97027)     대구광역시 동구 공산동     동구 공산동  2202071  
3       50kW  POINT (128.726065 35.96938)     대구광역시 동구 공산동     동구 공산동  2202071  
4        7kW  POINT (128.627216 35.91342)     대구광역시 북구 검단동     북구 검단동  2205070  
...      ...                          ...              ...        ...      ...  
50888   50kW  POINT (128.501556 35.81086)    대구광역시 달성군 화원읍    달성군 화원읍  2231011  
50889   50kW  POINT (128.501556 35.81086)    대구광역시 달성군 화원읍    달성군 화원읍  2231011  
50890    NaN  POINT (128.638144 35.84398)   대구광역시 수성구 황금1동   수성구 황금1동  2206061  
50891    NaN   POINT (128.64495 35.88186)    대구광역시 동구 효목1동    동구 효목1동  2202060  
50892  100kW  POINT (128.641241 35.87814)    대구광역시 동구 효목2동    동구 효목2동  2202061  

[50893 rows x 20 columns]

In [ ]:
alldata.dtypes

일자           object
충전소ID        object
충전소명칭        object
위도          float64
경도          float64
충전기ID         int64
충전기타입        object
사용횟수          int64
충전량         float64
year          int64
month         int64
day           int64
dayname      object
주소           object
충전기 형태       object
충전기 용량       object
geometry     object
adm_nm       object
gudong       object
adm_cd        int64
dtype: object

In [ ]:
alldata.isna().sum()

일자              0
충전소ID           0
충전소명칭           0
위도              0
경도              0
충전기ID           0
충전기타입           0
사용횟수            0
충전량             0
year            0
month           0
day             0
dayname         0
주소          20692
충전기 형태      20692
충전기 용량      20692
geometry        0
adm_nm          0
gudong          0
adm_cd          0
dtype: int64

##충전소 수 시각화

In [ ]:
alldata.head(1)

일자     충전소ID     충전소명칭        위도          경도  충전기ID 충전기타입  사용횟수  \
0  2023-08-31  27140008  DTC섬유박물관  35.91898  128.639976      1    급속     2   

     충전량  year  month  day   dayname                                    주소  \
0  40.16  2023      8   31  Thursday  대구광역시 동구 팔공로 227DTC섬유박물관(봉무동 1560-1)   

            충전기 형태 충전기 용량                     geometry           adm_nm  \
0  DC차데모+AC3상+DC콤보   50kW  POINT (128.639976 35.91898)  대구광역시 동구 불로·봉무동   

      gudong   adm_cd  
0  동구 불로·봉무동  2202063

In [ ]:
cs_count = alldata.groupby('adm_cd')['충전소ID'].count().reset_index()
cs_count

adm_cd  충전소ID
0    2201054    171
1    2201062   1070
2    2201065    180
3    2201066    172
4    2201067     49
..       ...    ...
105  2231015    536
106  2231016    194
107  2231031    221
108  2231032    171
109  2231036    335

[110 rows x 2 columns]

In [ ]:
cs_count2 = pd.merge(cs_count, df_emd2, how='left', on='adm_cd')
cs_count2

adm_cd  충전소ID   gudong
0    2201054    171   중구 삼덕동
1    2201062   1070   중구 대신동
2    2201065    180  중구 남산2동
3    2201066    172  중구 남산3동
4    2201067     49  중구 남산4동
..       ...    ...      ...
105  2231015    536  달성군 옥포읍
106  2231016    194  달성군 현풍읍
107  2231031    221  달성군 가창면
108  2231032    171  달성군 하빈면
109  2231036    335  달성군 구지면

[110 rows x 3 columns]

In [ ]:
cs_count['충전소ID'].sort_values()

4       49
34      63
67      81
29     118
53     128
      ... 
6     1620
57    1683
80    1704
88    1776
33    2294
Name: 충전소ID, Length: 110, dtype: int64

In [ ]:
# 대구시 위도, 경도
loc = (35.8714354, 128.601445)

m = folium.Map(location = loc, zoom_start = 11)

# geojson 데이터 dict 파싱
with open('/content/hangjeongdong_대구광역시.geojson', mode='r', encoding='utf-8') as f:
    geo_dong = json.loads(f.read())

# choropleth 시각화
folium.Choropleth(geo_data = geo_dong
                 , data = cs_count2
                 , columns = ['adm_cd', '충전소ID']
                 , key_on = 'properties.adm_cd'
                 , legend_name = '행정동별 충전소 수'
                 , fill_color = 'YlOrRd'
                 , fill_opacity = 0.5     # 투명도
                 , line_opacity = 0.5     # 라인 투명도
                 ).add_to(m)

style_function = lambda x: {'fillColor': '#ffffff',
                            'color':'#000000',
                            'fillOpacity': 0.1,
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000',
                                'color':'#000000',
                                'fillOpacity': 0.50,
                                'weight': 0.1}

NIL = folium.features.GeoJson(
    dg_geo,
    style_function=style_function,
    control=False,
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
        fields=['adm_nm'],
        aliases=['동이름: '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")
    )
)
m.add_child(NIL)
m.keep_in_front(NIL)

m

In [ ]:
m.save("행정동별충전소수.html")

##충전소 없는 동만 추

In [ ]:
cs_count2


adm_cd  충전소ID   gudong
0    2201054    171   중구 삼덕동
1    2201062   1070   중구 대신동
2    2201065    180  중구 남산2동
3    2201066    172  중구 남산3동
4    2201067     49  중구 남산4동
..       ...    ...      ...
105  2231015    536  달성군 옥포읍
106  2231016    194  달성군 현풍읍
107  2231031    221  달성군 가창면
108  2231032    171  달성군 하빈면
109  2231036    335  달성군 구지면

[110 rows x 3 columns]

In [ ]:
idx = cs_count2['충전소ID'].sort_values(ascending=False)[:15].index

In [ ]:
rank_cs = cs_count2.loc[idx, :][['gudong', '충전소ID']]
rank_cs

gudong  충전소ID
33    서구 상중이동   2294
88   달서구 월성2동   1776
80   수성구 고산2동   1704
57     북구 관문동   1683
6      중구 동인동   1620
99    달서구 성당동   1521
50    북구 산격2동   1275
104   달성군 유가읍   1217
51    북구 산격4동   1132
97   달서구 용산1동   1077
103   달성군 다사읍   1077
1      중구 대신동   1070
48    북구 침산3동    969
89    달서구 진천동    968
21     동구 공산동    960

In [ ]:
score_list = []
for i in range(len(rank_cs)):
    score_list.append(i+1)

score_list = score_list[::-1]
score_list

[15, 14, 13, 12, 11, 10, 9, 8, 7, 6, 5, 4, 3, 2, 1]

In [ ]:
rank_cs['score'] = score_list
rank_cs

gudong  충전소ID  score
33    서구 상중이동   2294     15
88   달서구 월성2동   1776     14
80   수성구 고산2동   1704     13
57     북구 관문동   1683     12
6      중구 동인동   1620     11
99    달서구 성당동   1521     10
50    북구 산격2동   1275      9
104   달성군 유가읍   1217      8
51    북구 산격4동   1132      7
97   달서구 용산1동   1077      6
103   달성군 다사읍   1077      5
1      중구 대신동   1070      4
48    북구 침산3동    969      3
89    달서구 진천동    968      2
21     동구 공산동    960      1

In [ ]:
rank_cs.to_csv('rank_충전소수별전기자동차대수순위.csv', encoding='cp949', index=False)

In [ ]:
cs_count2

adm_cd  충전소ID   gudong
0    2201054    171   중구 삼덕동
1    2201062   1070   중구 대신동
2    2201065    180  중구 남산2동
3    2201066    172  중구 남산3동
4    2201067     49  중구 남산4동
..       ...    ...      ...
105  2231015    536  달성군 옥포읍
106  2231016    194  달성군 현풍읍
107  2231031    221  달성군 가창면
108  2231032    171  달성군 하빈면
109  2231036    335  달성군 구지면

[110 rows x 3 columns]

In [ ]:
df_emd2

gudong   adm_cd
1     중구 삼덕동  2201054
2    중구 성내1동  2201056
3    중구 성내2동  2201059
4    중구 성내3동  2201061
5     중구 대신동  2201062
..       ...      ...
144  달성군 가창면  2231031
145  달성군 하빈면  2231032
146  달성군 옥포읍  2231015
147  달성군 현풍읍  2231016
148  달성군 구지면  2231036

[141 rows x 2 columns]

In [ ]:
total_cs = pd.merge(df_emd2, cs_count2, how='left', on=['adm_cd', 'gudong'])
total_cs

gudong   adm_cd   충전소ID
0     중구 삼덕동  2201054   171.0
1    중구 성내1동  2201056     NaN
2    중구 성내2동  2201059     NaN
3    중구 성내3동  2201061     NaN
4     중구 대신동  2201062  1070.0
..       ...      ...     ...
136  달성군 가창면  2231031   221.0
137  달성군 하빈면  2231032   171.0
138  달성군 옥포읍  2231015   536.0
139  달성군 현풍읍  2231016   194.0
140  달성군 구지면  2231036   335.0

[141 rows x 3 columns]

In [ ]:
total_cs.isna().sum()

gudong     0
adm_cd     0
충전소ID     31
dtype: int64

In [ ]:
total_cs = total_cs.fillna(0)

In [ ]:
total_cs


gudong   adm_cd   충전소ID
0     중구 삼덕동  2201054   171.0
1    중구 성내1동  2201056     0.0
2    중구 성내2동  2201059     0.0
3    중구 성내3동  2201061     0.0
4     중구 대신동  2201062  1070.0
..       ...      ...     ...
136  달성군 가창면  2231031   221.0
137  달성군 하빈면  2231032   171.0
138  달성군 옥포읍  2231015   536.0
139  달성군 현풍읍  2231016   194.0
140  달성군 구지면  2231036   335.0

[141 rows x 3 columns]

In [ ]:
total_cs['충전소ID'] = total_cs['충전소ID'].astype('int64')
total_cs

gudong   adm_cd  충전소ID
0     중구 삼덕동  2201054    171
1    중구 성내1동  2201056      0
2    중구 성내2동  2201059      0
3    중구 성내3동  2201061      0
4     중구 대신동  2201062   1070
..       ...      ...    ...
136  달성군 가창면  2231031    221
137  달성군 하빈면  2231032    171
138  달성군 옥포읍  2231015    536
139  달성군 현풍읍  2231016    194
140  달성군 구지면  2231036    335

[141 rows x 3 columns]

In [ ]:
no_cs = total_cs[total_cs['충전소ID'] == 0]
no_cs

gudong   adm_cd  충전소ID
1      중구 성내1동  2201056      0
2      중구 성내2동  2201059      0
3      중구 성내3동  2201061      0
5      중구 남산1동  2201064      0
9      중구 대봉1동  2201068      0
17   동구 신천1·2동  2202056      0
19     동구 신천4동  2202059      0
31     동구 안심3동  2202076      0
34     서구 내당1동  2203051      0
38   서구 비산2·3동  2203055      0
40     서구 비산5동  2203057      0
41     서구 비산6동  2203058      0
44     서구 평리2동  2203061      0
46     서구 평리4동  2203063      0
47     서구 평리5동  2203064      0
48     서구 평리6동  2203065      0
55     남구 대명1동  2204056      0
60     남구 대명6동  2204061      0
62    남구 대명10동  2204065      0
67     북구 침산2동  2205056      0
71     북구 산격3동  2205063      0
85      북구 국우동  2205083      0
88    수성구 범어2동  2206052      0
89    수성구 범어3동  2206053      0
90    수성구 범어4동  2206054      0
94   수성구 수성1가동  2206058      0
96   수성구 수성4가동  2206060      0
106   수성구 범물2동  2206070      0
112    달서구 감삼동  2207057      0
113    달서구 죽전동  2207058      0
129   달서구 이곡2동  2207074      0

##자동차데이터

In [ ]:
df_car = pd.read_csv('/content/대구광역시_행정동별 전기차 등록대수_20231031.csv', encoding='cp949')
df_car

시도명              행정동명   승용  승합   특수  화물   총합계
0    대구     대구광역시 중구 동인동   170   0   18   1   189
1    대구     대구광역시 중구 삼덕동    49   0   10   0    59
2    대구    대구광역시 중구 성내1동   691   0  476   0  1167
3    대구    대구광역시 중구 성내2동   220   0   18   0   238
4    대구    대구광역시 중구 성내3동    72   0   27   0    99
..   ..               ...  ...  ..  ...  ..   ...
148  대구    대구광역시 군위군 부계면    31   0   20   0    51
149  대구    대구광역시 군위군 우보면    13   0    9   0    22
150  대구    대구광역시 군위군 의흥면    19   0    6   0    25
151  대구    대구광역시 군위군 산성면     8   0    7   0    15
152  대구  대구광역시 군위군 삼국유사면    10   0    4   0    14

[153 rows x 7 columns]

In [ ]:
df_car['gudong'] = df_car['행정동명'].str.replace('대구광역시 ', '')
df_car

시도명              행정동명   승용  승합   특수  화물   총합계      gudong
0    대구     대구광역시 중구 동인동   170   0   18   1   189     중구 동인동 
1    대구     대구광역시 중구 삼덕동    49   0   10   0    59     중구 삼덕동 
2    대구    대구광역시 중구 성내1동   691   0  476   0  1167    중구 성내1동 
3    대구    대구광역시 중구 성내2동   220   0   18   0   238    중구 성내2동 
4    대구    대구광역시 중구 성내3동    72   0   27   0    99    중구 성내3동 
..   ..               ...  ...  ..  ...  ..   ...         ...
148  대구    대구광역시 군위군 부계면    31   0   20   0    51    군위군 부계면 
149  대구    대구광역시 군위군 우보면    13   0    9   0    22    군위군 우보면 
150  대구    대구광역시 군위군 의흥면    19   0    6   0    25    군위군 의흥면 
151  대구    대구광역시 군위군 산성면     8   0    7   0    15    군위군 산성면 
152  대구  대구광역시 군위군 삼국유사면    10   0    4   0    14  군위군 삼국유사면 

[153 rows x 8 columns]

In [ ]:
df_ecar = df_car[['총합계', 'gudong']]
df_ecar

총합계      gudong
0     189     중구 동인동 
1      59     중구 삼덕동 
2    1167    중구 성내1동 
3     238    중구 성내2동 
4      99    중구 성내3동 
..    ...         ...
148    51    군위군 부계면 
149    22    군위군 우보면 
150    25    군위군 의흥면 
151    15    군위군 산성면 
152    14  군위군 삼국유사면 

[153 rows x 2 columns]

In [ ]:
df_ecar['gudong'] = df_ecar['gudong'].str.rstrip()
df_ecar['gudong'].tolist()

<ipython-input-140-514c7a271551>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_ecar['gudong'] = df_ecar['gudong'].str.rstrip()


['중구 동인동',
 '중구 삼덕동',
 '중구 성내1동',
 '중구 성내2동',
 '중구 성내3동',
 '중구 대신동',
 '중구 남산1동',
 '중구 남산2동',
 '중구 남산3동',
 '중구 남산4동',
 '중구 대봉1동',
 '중구 대봉2동',
 '동구 신암1동',
 '동구 신암2동',
 '동구 신암3동',
 '동구 신암4동',
 '동구 신암5동',
 '동구 신천1·2동',
 '동구 신천3동',
 '동구 신천4동',
 '동구 효목1동',
 '동구 효목2동',
 '동구 도평동',
 '동구 불로·봉무동',
 '동구 지저동',
 '동구 동촌동',
 '동구 방촌동',
 '동구 해안동',
 '동구 안심1동',
 '동구 안심2동',
 '동구 안심3동',
 '동구 안심3.4동',
 '동구 안심4동',
 '동구 혁신동',
 '동구 공산동',
 '서구 내당1동',
 '서구 내당2·3동',
 '서구 내당4동',
 '서구 비산1동',
 '서구 비산2·3동',
 '서구 비산4동',
 '서구 비산5동',
 '서구 비산6동',
 '서구 비산7동',
 '서구 평리1동',
 '서구 평리2동',
 '서구 평리3동',
 '서구 평리4동',
 '서구 평리5동',
 '서구 평리6동',
 '서구 상중이동',
 '서구 원대동',
 '남구 이천동',
 '남구 봉덕1동',
 '남구 봉덕2동',
 '남구 봉덕3동',
 '남구 대명1동',
 '남구 대명2동',
 '남구 대명3동',
 '남구 대명4동',
 '남구 대명5동',
 '남구 대명6동',
 '남구 대명9동',
 '남구 대명10동',
 '남구 대명11동',
 '북구 고성동',
 '북구 칠성동',
 '북구 침산1동',
 '북구 침산2동',
 '북구 침산3동',
 '북구 산격1동',
 '북구 산격2동',
 '북구 산격3동',
 '북구 산격4동',
 '북구 대현동',
 '북구 복현1동',
 '북구 복현2동',
 '북구 검단동',
 '북구 무태조야동',
 '북구 관문동',
 '북구 태전1동',
 '북구 태전2동',
 '북구 구암동',
 '북구 관음동'

In [ ]:
no_cs_car = pd.merge(no_cs, df_ecar, how='left', on='gudong')
no_cs_car

gudong   adm_cd  충전소ID   총합계
0     중구 성내1동  2201056      0  1167
1     중구 성내2동  2201059      0   238
2     중구 성내3동  2201061      0    99
3     중구 남산1동  2201064      0    40
4     중구 대봉1동  2201068      0    82
5   동구 신천1·2동  2202056      0    91
6     동구 신천4동  2202059      0   152
7     동구 안심3동  2202076      0   196
8     서구 내당1동  2203051      0    66
9   서구 비산2·3동  2203055      0    35
10    서구 비산5동  2203057      0    21
11    서구 비산6동  2203058      0    16
12    서구 평리2동  2203061      0    53
13    서구 평리4동  2203063      0   101
14    서구 평리5동  2203064      0    50
15    서구 평리6동  2203065      0    61
16    남구 대명1동  2204056      0    73
17    남구 대명6동  2204061      0    82
18   남구 대명10동  2204065      0    61
19    북구 침산2동  2205056      0   207
20    북구 산격3동  2205063      0    60
21     북구 국우동  2205083      0   355
22   수성구 범어2동  2206052      0   255
23   수성구 범어3동  2206053      0   207
24   수성구 범어4동  2206054      0   470
25  수성구 수성1가동  2206058      0   121
26  수성구 수성4가동  2206060      0   145
27   수성구 범물2동  2206070      0   191
28    달서구 감삼동  2207057      0   343
29    달서구 죽전동  2207058      0   100
30   달서구 이곡2동  2207074      0   345

In [ ]:
idx = no_cs_car['총합계'].sort_values(ascending=False)[:15].index

In [ ]:
rank_no_cs_car = no_cs_car.loc[idx, :][['gudong', '총합계']]
rank_no_cs_car

gudong   총합계
0     중구 성내1동  1167
24   수성구 범어4동   470
21     북구 국우동   355
30   달서구 이곡2동   345
28    달서구 감삼동   343
22   수성구 범어2동   255
1     중구 성내2동   238
19    북구 침산2동   207
23   수성구 범어3동   207
7     동구 안심3동   196
27   수성구 범물2동   191
6     동구 신천4동   152
26  수성구 수성4가동   145
25  수성구 수성1가동   121
13    서구 평리4동   101

In [ ]:
rank_no_cs_car['score'] = score_list
rank_no_cs_car

gudong   총합계  score
0     중구 성내1동  1167     15
24   수성구 범어4동   470     14
21     북구 국우동   355     13
30   달서구 이곡2동   345     12
28    달서구 감삼동   343     11
22   수성구 범어2동   255     10
1     중구 성내2동   238      9
19    북구 침산2동   207      8
23   수성구 범어3동   207      7
7     동구 안심3동   196      6
27   수성구 범물2동   191      5
6     동구 신천4동   152      4
26  수성구 수성4가동   145      3
25  수성구 수성1가동   121      2
13    서구 평리4동   101      1

In [ ]:
rank_no_cs_car.to_csv('rank_충전소없는동전기차개수.csv', encoding='cp949', index=False)

#**Vehicle-to-Parking Lot Ratio**

In [ ]:
import pandas as pd
import numpy as np
import geopandas as gpd
from tqdm import tqdm
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon
import folium
import seaborn as sns
from patsy import dmatrices
import statsmodels.api as sm;
from statsmodels.stats.outliers_influence import variance_inflation_factor
%matplotlib inline
from patsy import dmatrix
import json

##주차장데이터전처리

In [ ]:
#주차장 데이터
df_parking_raw = pd.read_csv('/content/대구광역시_부설주차장운영및개방공유정보_20221031.csv', encoding='cp949')
df_parking_raw.head()

주차장아이디   구군코드            주차장명 주차장구분 주차장유형              소재지도로명주소  \
0  2720000001  27200  대구가톨릭대학교병원 주차장    민영   자주식  대구광역시 남구 두류공원로17길 33   
1  2720000002  27200  경북예술고등학교 부설주차장    공영   자주식   대구광역시 남구 중앙대로47길 30   

                  소재지지번주소  주차구획수 급지구분 부제시행구분  ... 평일개방공유시작시각 평일개방공유종료시각  \
0  대구광역시 남구 대명동 산 321-1번지   1289  2급지    미시행  ...        NaN        NaN   
1   대구광역시 남구 대명동 1804-1번지     64  1급지    미시행  ...        NaN        NaN   

  토요일개방공유시작시간 토요일개방공유종료시간 일요일개방공유시작시간 일요일개방공유종료시간 개방공유특기사항         위도  \
0         NaN         NaN         NaN         NaN      NaN  35.843522   
1         NaN         NaN         NaN         NaN      NaN  35.854618   

           경도     데이터기준일자  
0  128.567838  2022-07-25  
1  128.588365  2022-09-23  

[2 rows x 43 columns]

In [ ]:
#자료형 확인
df_parking_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4765 entries, 0 to 4764
Data columns (total 43 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   주차장아이디       4765 non-null   int64  
 1   구군코드         4765 non-null   int64  
 2   주차장명         4765 non-null   object 
 3   주차장구분        4765 non-null   object 
 4   주차장유형        4765 non-null   object 
 5   소재지도로명주소     4765 non-null   object 
 6   소재지지번주소      4765 non-null   object 
 7   주차구획수        4765 non-null   int64  
 8   급지구분         4765 non-null   object 
 9   부제시행구분       4765 non-null   object 
 10  운영요일         4765 non-null   object 
 11  평일운영시작시각     4475 non-null   object 
 12  평일운영종료시각     4475 non-null   object 
 13  토요일운영시작시각    3580 non-null   object 
 14  토요일운영종료시각    3580 non-null   object 
 15  공휴일운영시작시각    3120 non-null   object 
 16  공휴일운영종료시각    3120 non-null   object 
 17  요금정보         4765 non-null   object 
 18  주차기본시간       362 non-null    float64
 19  주차기본요금

In [ ]:
#원하는 컬럼만 추출
df_parking_use = df_parking_raw.loc[:, ['주차장아이디', '구군코드', '주차장명', '주차장구분', '주차장유형', '소재지도로명주소',	'소재지지번주소',	'주차구획수',	'급지구분',	'위도',	'경도']]
df_parking_use.head()

주차장아이디   구군코드            주차장명 주차장구분 주차장유형              소재지도로명주소  \
0  2720000001  27200  대구가톨릭대학교병원 주차장    민영   자주식  대구광역시 남구 두류공원로17길 33   
1  2720000002  27200  경북예술고등학교 부설주차장    공영   자주식   대구광역시 남구 중앙대로47길 30   
2  2720000003  27200    봉덕초등학교 부설주차장    공영   자주식       대구광역시 남구 효성로 71   
3  2720000005  27200     복만네장터 부설주차장    민영   자주식     대구광역시 남구 대명남로 126   
4  2720000006  27200      성명초등학교 주차장    공영   자주식    대구광역시 남구 성당로30길 55   

                  소재지지번주소  주차구획수 급지구분         위도          경도  
0  대구광역시 남구 대명동 산 321-1번지   1289  2급지  35.843522  128.567838  
1   대구광역시 남구 대명동 1804-1번지     64  1급지  35.854618  128.588365  
2   대구광역시 남구 봉덕동 1319-1번지     60  3급지  35.839402  128.597509  
3    대구광역시 남구 대명동 623-2번지     13  3급지  35.834621  128.572458  
4     대구광역시 남구 대명동 3050번지     29  1급지  35.845836  128.570897

In [ ]:
#결측치 확인
df_parking_use.isna().sum()

주차장아이디      0
구군코드        0
주차장명        0
주차장구분       0
주차장유형       0
소재지도로명주소    0
소재지지번주소     0
주차구획수       0
급지구분        0
위도          0
경도          0
dtype: int64

In [ ]:
df_parking = df_parking_use

In [ ]:
dg_geo = gpd.read_file('/content/hangjeongdong_대구광역시.geojson')
dg_geo

OBJECTID         adm_nm   adm_cd     adm_cd2    sgg sido sidonm sggnm  \
0         625   대구광역시 중구 삼덕동  2201054  2711054500  27110   27  대구광역시    중구   
1         626  대구광역시 중구 성내1동  2201056  2711056500  27110   27  대구광역시    중구   
2         627  대구광역시 중구 성내2동  2201059  2711057500  27110   27  대구광역시    중구   
3         628  대구광역시 중구 성내3동  2201061  2711058500  27110   27  대구광역시    중구   
4         629   대구광역시 중구 대신동  2201062  2711059500  27110   27  대구광역시    중구   
..        ...            ...      ...         ...    ...  ...    ...   ...   
136       761  대구광역시 달성군 현풍읍  2231016  2771026500  27710   27  대구광역시   달성군   
137       762  대구광역시 달성군 유가읍  2231014  2771025900  27710   27  대구광역시   달성군   
138       763  대구광역시 달성군 구지면  2231036  2771038000  27710   27  대구광역시   달성군   
139      3489  대구광역시 동구 안심3동  2202076  2714074200  27140   27  대구광역시    동구   
140      3490   대구광역시 동구 혁신동  2202078  2714075500  27140   27  대구광역시    동구   

                                              geometry  
0    MULTIPOLYGON (((128.59981 35.86827, 128.60252 ...  
1    MULTIPOLYGON (((128.60136 35.8748, 128.59981 3...  
2    MULTIPOLYGON (((128.59495 35.8753, 128.59407 3...  
3    MULTIPOLYGON (((128.58017 35.87908, 128.58838 ...  
4    MULTIPOLYGON (((128.58261 35.87059, 128.58235 ...  
..                                                 ...  
136  MULTIPOLYGON (((128.4571 35.7156, 128.45764 35...  
137  MULTIPOLYGON (((128.52314 35.71888, 128.52337 ...  
138  MULTIPOLYGON (((128.37517 35.70249, 128.37478 ...  
139  MULTIPOLYGON (((128.73427 35.87484, 128.73604 ...  
140  MULTIPOLYGON (((128.73427 35.87484, 128.72756 ...  

[141 rows x 9 columns]

In [ ]:
dg_geo['geometry']

0      MULTIPOLYGON (((128.59981 35.86827, 128.60252 ...
1      MULTIPOLYGON (((128.60136 35.8748, 128.59981 3...
2      MULTIPOLYGON (((128.59495 35.8753, 128.59407 3...
3      MULTIPOLYGON (((128.58017 35.87908, 128.58838 ...
4      MULTIPOLYGON (((128.58261 35.87059, 128.58235 ...
                             ...                        
136    MULTIPOLYGON (((128.4571 35.7156, 128.45764 35...
137    MULTIPOLYGON (((128.52314 35.71888, 128.52337 ...
138    MULTIPOLYGON (((128.37517 35.70249, 128.37478 ...
139    MULTIPOLYGON (((128.73427 35.87484, 128.73604 ...
140    MULTIPOLYGON (((128.73427 35.87484, 128.72756 ...
Name: geometry, Length: 141, dtype: geometry

In [ ]:
def find_admin_area(point, admin_areas):
    for index, row in admin_areas.iterrows():
        if row['geometry'].contains(point):
            return row['adm_nm']
    return None

In [ ]:
df_parking['geometry'] = [Point(xy) for xy in zip(df_parking['경도'], df_parking['위도'])]
df_parking.head(1)

주차장아이디   구군코드            주차장명 주차장구분 주차장유형              소재지도로명주소  \
0  2720000001  27200  대구가톨릭대학교병원 주차장    민영   자주식  대구광역시 남구 두류공원로17길 33   

                  소재지지번주소  주차구획수 급지구분         위도          경도  \
0  대구광역시 남구 대명동 산 321-1번지   1289  2급지  35.843522  128.567838   

                       geometry  
0  POINT (128.567838 35.843522)

In [ ]:
df_parking['adm_nm'] = df_parking['geometry'].apply(lambda x: find_admin_area(x, dg_geo))
df_parking.head(1)

주차장아이디   구군코드            주차장명 주차장구분 주차장유형              소재지도로명주소  \
0  2720000001  27200  대구가톨릭대학교병원 주차장    민영   자주식  대구광역시 남구 두류공원로17길 33   

                  소재지지번주소  주차구획수 급지구분         위도          경도  \
0  대구광역시 남구 대명동 산 321-1번지   1289  2급지  35.843522  128.567838   

                       geometry         adm_nm  
0  POINT (128.567838 35.843522)  대구광역시 남구 대명4동

In [ ]:
df_parking.isna().sum()

주차장아이디      0
구군코드        0
주차장명        0
주차장구분       0
주차장유형       0
소재지도로명주소    0
소재지지번주소     0
주차구획수       0
급지구분        0
위도          0
경도          0
geometry    0
adm_nm      0
dtype: int64

In [ ]:
df_parking.to_csv('전처리주차장.csv', index=False, encoding='cp949')

In [ ]:
#amd_cd와 동을 join
df_parking['gudong'] = df_parking['adm_nm'].str.replace('대구광역시 ', '')
df_parking

주차장아이디   구군코드            주차장명 주차장구분    주차장유형  \
0     2720000001  27200  대구가톨릭대학교병원 주차장    민영      자주식   
1     2720000002  27200  경북예술고등학교 부설주차장    공영      자주식   
2     2720000003  27200    봉덕초등학교 부설주차장    공영      자주식   
3     2720000005  27200     복만네장터 부설주차장    민영      자주식   
4     2720000006  27200      성명초등학교 주차장    공영      자주식   
...          ...    ...             ...   ...      ...   
4760  2771000495  27710     명곡리 166 주차장    민영      자주식   
4761  2771000519  27710        화인타워 주차장    민영  자주식+기계식   
4762  2771000554  27710    도케비커피 본점 주차장    민영      자주식   
4763  2771000361  27710        동명테크 주차장    민영      자주식   
4764  2771000362  27710        태주빌딩 주차장    민영      자주식   

                          소재지도로명주소                      소재지지번주소  주차구획수 급지구분  \
0             대구광역시 남구 두류공원로17길 33       대구광역시 남구 대명동 산 321-1번지   1289  2급지   
1              대구광역시 남구 중앙대로47길 30        대구광역시 남구 대명동 1804-1번지     64  1급지   
2                  대구광역시 남구 효성로 71        대구광역시 남구 봉덕동 1319-1번지     60  3급지   
3                대구광역시 남구 대명남로 126         대구광역시 남구 대명동 623-2번지     13  3급지   
4               대구광역시 남구 성당로30길 55          대구광역시 남구 대명동 3050번지     29  1급지   
...                            ...                          ...    ...  ...   
4760         대구광역시 달성군 화원읍 명천로 206      대구광역시 달성군 화원읍 명곡리 166번지     24  3급지   
4761  대구광역시 달성군 구지면 국가산단대로42길 5-23     대구광역시 달성군 구지면 응암리 1275번지     77  3급지   
4762      대구광역시 달성군 유가읍 음동길 130-15        대구광역시 달성군 유가읍 음리 65번지     43  3급지   
4763        대구광역시 달성군 하빈면 하빈남로 596  대구광역시 달성군 하빈면 하산리 1100-10번지     20  3급지   
4764          대구광역시 달성군 다사읍 세천북로 5   대구광역시 달성군 다사읍 세천리 1578-6번지     10  3급지   

             위도          경도                      geometry         adm_nm  \
0     35.843522  128.567838  POINT (128.567838 35.843522)  대구광역시 남구 대명4동   
1     35.854618  128.588365  POINT (128.588365 35.854618)  대구광역시 남구 대명2동   
2     35.839402  128.597509  POINT (128.597509 35.839402)  대구광역시 남구 봉덕3동   
3     35.834621  128.572458  POINT (128.572458 35.834621)  대구광역시 남구 대명9동   
4     35.845836  128.570897  POINT (128.570897 35.845836)  대구광역시 남구 대명4동   
...         ...         ...                           ...            ...   
4760  35.799941  128.495944  POINT (128.495944 35.799941)  대구광역시 달성군 화원읍   
4761  35.649410  128.418176   POINT (128.418176 35.64941)  대구광역시 달성군 구지면   
4762  35.697960  128.488249   POINT (128.488249 35.69796)  대구광역시 달성군 유가읍   
4763  35.878069  128.398147  POINT (128.398147 35.878069)  대구광역시 달성군 하빈면   
4764  35.875127  128.478549  POINT (128.478549 35.875127)  대구광역시 달성군 다사읍   

       gudong  
0     남구 대명4동  
1     남구 대명2동  
2     남구 봉덕3동  
3     남구 대명9동  
4     남구 대명4동  
...       ...  
4760  달성군 화원읍  
4761  달성군 구지면  
4762  달성군 유가읍  
4763  달성군 하빈면  
4764  달성군 다사읍  

[4765 rows x 14 columns]

In [ ]:
df_emd = pd.read_csv('대구광역시_읍면동코드.csv', encoding='cp949')
df_emd

sido    ssg   gu     adm_cd  dong
0    대구광역시  22010   중구        NaN   NaN
1    대구광역시  22010   중구  2201054.0   삼덕동
2    대구광역시  22010   중구  2201056.0  성내1동
3    대구광역시  22010   중구  2201059.0  성내2동
4    대구광역시  22010   중구  2201061.0  성내3동
..     ...    ...  ...        ...   ...
144  대구광역시  22310  달성군  2231031.0   가창면
145  대구광역시  22310  달성군  2231032.0   하빈면
146  대구광역시  22310  달성군  2231015.0   옥포읍
147  대구광역시  22310  달성군  2231016.0   현풍읍
148  대구광역시  22310  달성군  2231036.0   구지면

[149 rows x 5 columns]

In [ ]:
df_emd2 = df_emd[['gudong', 'adm_cd']]
df_emd2

KeyError: "['gudong'] not in index"

In [ ]:
df_emd2.dropna(inplace=True)
df_emd2

<ipython-input-173-f3fe0bdebc66>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_emd2.dropna(inplace=True)


gudong   adm_cd
1     중구 삼덕동  2201054
2    중구 성내1동  2201056
3    중구 성내2동  2201059
4    중구 성내3동  2201061
5     중구 대신동  2201062
..       ...      ...
144  달성군 가창면  2231031
145  달성군 하빈면  2231032
146  달성군 옥포읍  2231015
147  달성군 현풍읍  2231016
148  달성군 구지면  2231036

[141 rows x 2 columns]

In [ ]:
df_emd2['adm_cd'] = df_emd2['adm_cd'].astype('int64')
df_emd2

<ipython-input-174-1baa3fcb732e>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_emd2['adm_cd'] = df_emd2['adm_cd'].astype('int64')


gudong   adm_cd
1     중구 삼덕동  2201054
2    중구 성내1동  2201056
3    중구 성내2동  2201059
4    중구 성내3동  2201061
5     중구 대신동  2201062
..       ...      ...
144  달성군 가창면  2231031
145  달성군 하빈면  2231032
146  달성군 옥포읍  2231015
147  달성군 현풍읍  2231016
148  달성군 구지면  2231036

[141 rows x 2 columns]

In [ ]:
#parking과 emd merge
df_parking.head(1)

주차장아이디   구군코드            주차장명 주차장구분 주차장유형              소재지도로명주소  \
0  2720000001  27200  대구가톨릭대학교병원 주차장    민영   자주식  대구광역시 남구 두류공원로17길 33   

                  소재지지번주소  주차구획수 급지구분         위도          경도  \
0  대구광역시 남구 대명동 산 321-1번지   1289  2급지  35.843522  128.567838   

                       geometry         adm_nm   gudong  
0  POINT (128.567838 35.843522)  대구광역시 남구 대명4동  남구 대명4동

In [ ]:
alldata = pd.merge(df_parking, df_emd2, how='left', on='gudong')
alldata

주차장아이디   구군코드            주차장명 주차장구분    주차장유형  \
0     2720000001  27200  대구가톨릭대학교병원 주차장    민영      자주식   
1     2720000002  27200  경북예술고등학교 부설주차장    공영      자주식   
2     2720000003  27200    봉덕초등학교 부설주차장    공영      자주식   
3     2720000005  27200     복만네장터 부설주차장    민영      자주식   
4     2720000006  27200      성명초등학교 주차장    공영      자주식   
...          ...    ...             ...   ...      ...   
4760  2771000495  27710     명곡리 166 주차장    민영      자주식   
4761  2771000519  27710        화인타워 주차장    민영  자주식+기계식   
4762  2771000554  27710    도케비커피 본점 주차장    민영      자주식   
4763  2771000361  27710        동명테크 주차장    민영      자주식   
4764  2771000362  27710        태주빌딩 주차장    민영      자주식   

                          소재지도로명주소                      소재지지번주소  주차구획수 급지구분  \
0             대구광역시 남구 두류공원로17길 33       대구광역시 남구 대명동 산 321-1번지   1289  2급지   
1              대구광역시 남구 중앙대로47길 30        대구광역시 남구 대명동 1804-1번지     64  1급지   
2                  대구광역시 남구 효성로 71        대구광역시 남구 봉덕동 1319-1번지     60  3급지   
3                대구광역시 남구 대명남로 126         대구광역시 남구 대명동 623-2번지     13  3급지   
4               대구광역시 남구 성당로30길 55          대구광역시 남구 대명동 3050번지     29  1급지   
...                            ...                          ...    ...  ...   
4760         대구광역시 달성군 화원읍 명천로 206      대구광역시 달성군 화원읍 명곡리 166번지     24  3급지   
4761  대구광역시 달성군 구지면 국가산단대로42길 5-23     대구광역시 달성군 구지면 응암리 1275번지     77  3급지   
4762      대구광역시 달성군 유가읍 음동길 130-15        대구광역시 달성군 유가읍 음리 65번지     43  3급지   
4763        대구광역시 달성군 하빈면 하빈남로 596  대구광역시 달성군 하빈면 하산리 1100-10번지     20  3급지   
4764          대구광역시 달성군 다사읍 세천북로 5   대구광역시 달성군 다사읍 세천리 1578-6번지     10  3급지   

             위도          경도                      geometry         adm_nm  \
0     35.843522  128.567838  POINT (128.567838 35.843522)  대구광역시 남구 대명4동   
1     35.854618  128.588365  POINT (128.588365 35.854618)  대구광역시 남구 대명2동   
2     35.839402  128.597509  POINT (128.597509 35.839402)  대구광역시 남구 봉덕3동   
3     35.834621  128.572458  POINT (128.572458 35.834621)  대구광역시 남구 대명9동   
4     35.845836  128.570897  POINT (128.570897 35.845836)  대구광역시 남구 대명4동   
...         ...         ...                           ...            ...   
4760  35.799941  128.495944  POINT (128.495944 35.799941)  대구광역시 달성군 화원읍   
4761  35.649410  128.418176   POINT (128.418176 35.64941)  대구광역시 달성군 구지면   
4762  35.697960  128.488249   POINT (128.488249 35.69796)  대구광역시 달성군 유가읍   
4763  35.878069  128.398147  POINT (128.398147 35.878069)  대구광역시 달성군 하빈면   
4764  35.875127  128.478549  POINT (128.478549 35.875127)  대구광역시 달성군 다사읍   

       gudong   adm_cd  
0     남구 대명4동  2204059  
1     남구 대명2동  2204057  
2     남구 봉덕3동  2204055  
3     남구 대명9동  2204064  
4     남구 대명4동  2204059  
...       ...      ...  
4760  달성군 화원읍  2231011  
4761  달성군 구지면  2231036  
4762  달성군 유가읍  2231014  
4763  달성군 하빈면  2231032  
4764  달성군 다사읍  2231013  

[4765 rows x 15 columns]

In [ ]:
alldata.dtypes

주차장아이디        int64
구군코드          int64
주차장명         object
주차장구분        object
주차장유형        object
소재지도로명주소     object
소재지지번주소      object
주차구획수         int64
급지구분         object
위도          float64
경도          float64
geometry     object
adm_nm       object
gudong       object
adm_cd        int64
dtype: object

In [ ]:
alldata.isna().sum()

주차장아이디      0
구군코드        0
주차장명        0
주차장구분       0
주차장유형       0
소재지도로명주소    0
소재지지번주소     0
주차구획수       0
급지구분        0
위도          0
경도          0
geometry    0
adm_nm      0
gudong      0
adm_cd      0
dtype: int64

In [ ]:
#주차장수 시각화
alldata.head(1)

주차장아이디   구군코드            주차장명 주차장구분 주차장유형              소재지도로명주소  \
0  2720000001  27200  대구가톨릭대학교병원 주차장    민영   자주식  대구광역시 남구 두류공원로17길 33   

                  소재지지번주소  주차구획수 급지구분         위도          경도  \
0  대구광역시 남구 대명동 산 321-1번지   1289  2급지  35.843522  128.567838   

                       geometry         adm_nm   gudong   adm_cd  
0  POINT (128.567838 35.843522)  대구광역시 남구 대명4동  남구 대명4동  2204059

In [ ]:
park_count = alldata.groupby('adm_cd')['주차구획수'].sum().reset_index()
park_count

adm_cd  주차구획수
0    2201054   3487
1    2201056   4750
2    2201059   6799
3    2201061    259
4    2201062   1301
..       ...    ...
136  2231015    937
137  2231016   3238
138  2231031   2291
139  2231032    850
140  2231036   2321

[141 rows x 2 columns]

In [ ]:
park_count2 = pd.merge(park_count, df_emd2, how='left', on='adm_cd')
park_count2

adm_cd  주차구획수   gudong
0    2201054   3487   중구 삼덕동
1    2201056   4750  중구 성내1동
2    2201059   6799  중구 성내2동
3    2201061    259  중구 성내3동
4    2201062   1301   중구 대신동
..       ...    ...      ...
136  2231015    937  달성군 옥포읍
137  2231016   3238  달성군 현풍읍
138  2231031   2291  달성군 가창면
139  2231032    850  달성군 하빈면
140  2231036   2321  달성군 구지면

[141 rows x 3 columns]

In [ ]:
# 대구시 위도, 경도
loc = (35.8714354, 128.601445)

m = folium.Map(location = loc, zoom_start = 11)

# geojson 데이터 dict 파싱
with open('/content/hangjeongdong_대구광역시.geojson', mode='r', encoding='utf-8') as f:
    geo_dong = json.loads(f.read())

# choropleth 시각화
folium.Choropleth(geo_data = geo_dong
                 , data = park_count2
                 , columns = ['adm_cd', '주차구획수']
                 , key_on = 'properties.adm_cd'
                 , legend_name = '행정동별 주차장 수'
                 , fill_color = 'YlOrRd'
                 , fill_opacity = 0.5     # 투명도
                 , line_opacity = 0.5     # 라인 투명도
                 ).add_to(m)

style_function = lambda x: {'fillColor': '#ffffff',
                            'color':'#000000',
                            'fillOpacity': 0.1,
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000',
                                'color':'#000000',
                                'fillOpacity': 0.50,
                                'weight': 0.1}

NIL = folium.features.GeoJson(
    dg_geo,
    style_function=style_function,
    control=False,
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
        fields=['adm_nm'],
        aliases=['동이름: '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")
    )
)
m.add_child(NIL)
m.keep_in_front(NIL)

m

##자동차 수

In [ ]:
df_car = pd.read_csv('/content/대구광역시_행정동별 전기차 등록대수_20231031.csv', encoding='cp949')
df_car

시도명              행정동명   승용  승합   특수  화물   총합계
0    대구     대구광역시 중구 동인동   170   0   18   1   189
1    대구     대구광역시 중구 삼덕동    49   0   10   0    59
2    대구    대구광역시 중구 성내1동   691   0  476   0  1167
3    대구    대구광역시 중구 성내2동   220   0   18   0   238
4    대구    대구광역시 중구 성내3동    72   0   27   0    99
..   ..               ...  ...  ..  ...  ..   ...
148  대구    대구광역시 군위군 부계면    31   0   20   0    51
149  대구    대구광역시 군위군 우보면    13   0    9   0    22
150  대구    대구광역시 군위군 의흥면    19   0    6   0    25
151  대구    대구광역시 군위군 산성면     8   0    7   0    15
152  대구  대구광역시 군위군 삼국유사면    10   0    4   0    14

[153 rows x 7 columns]

In [ ]:
df_car['gudong'] = df_car['행정동명'].str.replace('대구광역시 ', '')
df_car

시도명              행정동명   승용  승합   특수  화물   총합계      gudong
0    대구     대구광역시 중구 동인동   170   0   18   1   189     중구 동인동 
1    대구     대구광역시 중구 삼덕동    49   0   10   0    59     중구 삼덕동 
2    대구    대구광역시 중구 성내1동   691   0  476   0  1167    중구 성내1동 
3    대구    대구광역시 중구 성내2동   220   0   18   0   238    중구 성내2동 
4    대구    대구광역시 중구 성내3동    72   0   27   0    99    중구 성내3동 
..   ..               ...  ...  ..  ...  ..   ...         ...
148  대구    대구광역시 군위군 부계면    31   0   20   0    51    군위군 부계면 
149  대구    대구광역시 군위군 우보면    13   0    9   0    22    군위군 우보면 
150  대구    대구광역시 군위군 의흥면    19   0    6   0    25    군위군 의흥면 
151  대구    대구광역시 군위군 산성면     8   0    7   0    15    군위군 산성면 
152  대구  대구광역시 군위군 삼국유사면    10   0    4   0    14  군위군 삼국유사면 

[153 rows x 8 columns]

In [ ]:
df_ecar = df_car[['gudong', '총합계']]

In [ ]:
df_ecar.columns = ['gudong', '전기차대수']

In [ ]:
df_ecar

gudong  전기차대수
0       중구 동인동     189
1       중구 삼덕동      59
2      중구 성내1동    1167
3      중구 성내2동     238
4      중구 성내3동      99
..          ...    ...
148    군위군 부계면      51
149    군위군 우보면      22
150    군위군 의흥면      25
151    군위군 산성면      15
152  군위군 삼국유사면      14

[153 rows x 2 columns]

In [ ]:
df_ecar['gudong'].tolist()

['중구 동인동 ',
 '중구 삼덕동 ',
 '중구 성내1동 ',
 '중구 성내2동 ',
 '중구 성내3동 ',
 '중구 대신동 ',
 '중구 남산1동 ',
 '중구 남산2동 ',
 '중구 남산3동 ',
 '중구 남산4동 ',
 '중구 대봉1동 ',
 '중구 대봉2동 ',
 '동구 신암1동 ',
 '동구 신암2동 ',
 '동구 신암3동 ',
 '동구 신암4동 ',
 '동구 신암5동 ',
 '동구 신천1·2동 ',
 '동구 신천3동 ',
 '동구 신천4동 ',
 '동구 효목1동 ',
 '동구 효목2동 ',
 '동구 도평동 ',
 '동구 불로·봉무동 ',
 '동구 지저동 ',
 '동구 동촌동 ',
 '동구 방촌동 ',
 '동구 해안동 ',
 '동구 안심1동 ',
 '동구 안심2동 ',
 '동구 안심3동 ',
 '동구 안심3.4동 ',
 '동구 안심4동 ',
 '동구 혁신동 ',
 '동구 공산동 ',
 '서구 내당1동 ',
 '서구 내당2·3동 ',
 '서구 내당4동 ',
 '서구 비산1동 ',
 '서구 비산2·3동 ',
 '서구 비산4동 ',
 '서구 비산5동 ',
 '서구 비산6동 ',
 '서구 비산7동 ',
 '서구 평리1동 ',
 '서구 평리2동 ',
 '서구 평리3동 ',
 '서구 평리4동 ',
 '서구 평리5동 ',
 '서구 평리6동 ',
 '서구 상중이동 ',
 '서구 원대동 ',
 '남구 이천동 ',
 '남구 봉덕1동 ',
 '남구 봉덕2동 ',
 '남구 봉덕3동 ',
 '남구 대명1동 ',
 '남구 대명2동 ',
 '남구 대명3동 ',
 '남구 대명4동 ',
 '남구 대명5동 ',
 '남구 대명6동 ',
 '남구 대명9동 ',
 '남구 대명10동 ',
 '남구 대명11동 ',
 '북구 고성동 ',
 '북구 칠성동 ',
 '북구 침산1동 ',
 '북구 침산2동 ',
 '북구 침산3동 ',
 '북구 산격1동 ',
 '북구 산격2동 ',
 '북구 산격3동 ',
 '북구 산격4동 ',
 '북구 대현동 ',
 '북구 복현1동 ',
 '북구 복현2동 ',
 '

In [ ]:
df_ecar['gudong'] = df_ecar['gudong'].str.rstrip()
df_ecar['gudong'].tolist()

<ipython-input-189-514c7a271551>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_ecar['gudong'] = df_ecar['gudong'].str.rstrip()


['중구 동인동',
 '중구 삼덕동',
 '중구 성내1동',
 '중구 성내2동',
 '중구 성내3동',
 '중구 대신동',
 '중구 남산1동',
 '중구 남산2동',
 '중구 남산3동',
 '중구 남산4동',
 '중구 대봉1동',
 '중구 대봉2동',
 '동구 신암1동',
 '동구 신암2동',
 '동구 신암3동',
 '동구 신암4동',
 '동구 신암5동',
 '동구 신천1·2동',
 '동구 신천3동',
 '동구 신천4동',
 '동구 효목1동',
 '동구 효목2동',
 '동구 도평동',
 '동구 불로·봉무동',
 '동구 지저동',
 '동구 동촌동',
 '동구 방촌동',
 '동구 해안동',
 '동구 안심1동',
 '동구 안심2동',
 '동구 안심3동',
 '동구 안심3.4동',
 '동구 안심4동',
 '동구 혁신동',
 '동구 공산동',
 '서구 내당1동',
 '서구 내당2·3동',
 '서구 내당4동',
 '서구 비산1동',
 '서구 비산2·3동',
 '서구 비산4동',
 '서구 비산5동',
 '서구 비산6동',
 '서구 비산7동',
 '서구 평리1동',
 '서구 평리2동',
 '서구 평리3동',
 '서구 평리4동',
 '서구 평리5동',
 '서구 평리6동',
 '서구 상중이동',
 '서구 원대동',
 '남구 이천동',
 '남구 봉덕1동',
 '남구 봉덕2동',
 '남구 봉덕3동',
 '남구 대명1동',
 '남구 대명2동',
 '남구 대명3동',
 '남구 대명4동',
 '남구 대명5동',
 '남구 대명6동',
 '남구 대명9동',
 '남구 대명10동',
 '남구 대명11동',
 '북구 고성동',
 '북구 칠성동',
 '북구 침산1동',
 '북구 침산2동',
 '북구 침산3동',
 '북구 산격1동',
 '북구 산격2동',
 '북구 산격3동',
 '북구 산격4동',
 '북구 대현동',
 '북구 복현1동',
 '북구 복현2동',
 '북구 검단동',
 '북구 무태조야동',
 '북구 관문동',
 '북구 태전1동',
 '북구 태전2동',
 '북구 구암동',
 '북구 관음동'

In [ ]:
park_count2

adm_cd  주차구획수   gudong
0    2201054   3487   중구 삼덕동
1    2201056   4750  중구 성내1동
2    2201059   6799  중구 성내2동
3    2201061    259  중구 성내3동
4    2201062   1301   중구 대신동
..       ...    ...      ...
136  2231015    937  달성군 옥포읍
137  2231016   3238  달성군 현풍읍
138  2231031   2291  달성군 가창면
139  2231032    850  달성군 하빈면
140  2231036   2321  달성군 구지면

[141 rows x 3 columns]

In [ ]:
park_ecar = pd.merge(park_count2, df_ecar, how='left', on='gudong')
park_ecar

adm_cd  주차구획수   gudong  전기차대수
0    2201054   3487   중구 삼덕동     59
1    2201056   4750  중구 성내1동   1167
2    2201059   6799  중구 성내2동    238
3    2201061    259  중구 성내3동     99
4    2201062   1301   중구 대신동     88
..       ...    ...      ...    ...
136  2231015    937  달성군 옥포읍    358
137  2231016   3238  달성군 현풍읍    270
138  2231031   2291  달성군 가창면    129
139  2231032    850  달성군 하빈면    102
140  2231036   2321  달성군 구지면    377

[141 rows x 4 columns]

In [ ]:
# 잘 합쳐졌는지 확인
park_ecar.isna().sum()

adm_cd    0
주차구획수     0
gudong    0
전기차대수     0
dtype: int64

In [ ]:
# 대구시 위도, 경도
loc = (35.8714354, 128.601445)

m = folium.Map(location = loc, zoom_start = 11)

# geojson 데이터 dict 파싱
with open('/content/hangjeongdong_대구광역시.geojson', mode='r', encoding='utf-8') as f:
    geo_dong = json.loads(f.read())

# choropleth 시각화
folium.Choropleth(geo_data = geo_dong
                 , data = park_ecar
                 , columns = ['adm_cd', '전기차대수']
                 , key_on = 'properties.adm_cd'
                 , legend_name = '행정동별 전기차 수'
                 , fill_color = 'YlOrRd'
                 , fill_opacity = 0.5     # 투명도
                 , line_opacity = 0.5     # 라인 투명도
                 ).add_to(m)

style_function = lambda x: {'fillColor': '#ffffff',
                            'color':'#000000',
                            'fillOpacity': 0.1,
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000',
                                'color':'#000000',
                                'fillOpacity': 0.50,
                                'weight': 0.1}

NIL = folium.features.GeoJson(
    dg_geo,
    style_function=style_function,
    control=False,
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
        fields=['adm_nm'],
        aliases=['동이름: '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")
    )
)
m.add_child(NIL)
m.keep_in_front(NIL)

m

In [ ]:
# 주차장구획수 합계 / 동별 전기자동차대수
park_ecar['ratio'] = park_ecar['주차구획수'] / park_ecar['전기차대수']
park_ecar

adm_cd  주차구획수   gudong  전기차대수      ratio
0    2201054   3487   중구 삼덕동     59  59.101695
1    2201056   4750  중구 성내1동   1167   4.070266
2    2201059   6799  중구 성내2동    238  28.567227
3    2201061    259  중구 성내3동     99   2.616162
4    2201062   1301   중구 대신동     88  14.784091
..       ...    ...      ...    ...        ...
136  2231015    937  달성군 옥포읍    358   2.617318
137  2231016   3238  달성군 현풍읍    270  11.992593
138  2231031   2291  달성군 가창면    129  17.759690
139  2231032    850  달성군 하빈면    102   8.333333
140  2231036   2321  달성군 구지면    377   6.156499

[141 rows x 5 columns]

In [ ]:
# 대구시 위도, 경도
loc = (35.8714354, 128.601445)

m = folium.Map(location = loc, zoom_start = 11)

# geojson 데이터 dict 파싱
with open('/content/hangjeongdong_대구광역시.geojson', mode='r', encoding='utf-8') as f:
    geo_dong = json.loads(f.read())

# choropleth 시각화
folium.Choropleth(geo_data = geo_dong
                 , data = park_ecar
                 , columns = ['adm_cd', 'ratio']
                 , key_on = 'properties.adm_cd'
                 , legend_name = '전기차 1대별 주차장 개수'
                 , fill_color = 'YlOrRd'
                 , fill_opacity = 0.5     # 투명도
                 , line_opacity = 0.5     # 라인 투명도
                 ).add_to(m)

style_function = lambda x: {'fillColor': '#ffffff',
                            'color':'#000000',
                            'fillOpacity': 0.1,
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000',
                                'color':'#000000',
                                'fillOpacity': 0.50,
                                'weight': 0.1}

NIL = folium.features.GeoJson(
    dg_geo,
    style_function=style_function,
    control=False,
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
        fields=['adm_nm'],
        aliases=['동이름: '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")
    )
)
m.add_child(NIL)
m.keep_in_front(NIL)

m